# Data Cleaning for OpenFoodFacts

## Dataset Description

Dataset Description...

In [1]:
# Import libraries

%matplotlib inline
import matplotlib.pyplot as plt

import numpy as np
import pandas as pd
import csv

#import re
import regex as re

import os
from pathlib import Path

In [2]:
# Parameters

path = str(Path(os.path.abspath(os.getcwd())).parent.absolute())
openfoodfactsUrl = path + '/data/en.openfoodfacts.org.products.csv'
foodtableUrl = path + '/data/data_2.tsv'

ingredients_tx = path + '/data/ingredients.txt'
additives_tx = path + '/data/additives.txt'
vitamins_tx = path + '/data/vitamins.txt'
packaging_materials_tx = path + '/data/packaging_materials.txt'
packaging_shapes_tx = path + '/data/packaging_shapes.txt'
labels_tx = path + '/data/labels.txt'

savePath =  path + '/data/foodDB/'

## Helper Functions

Helper functions...

In [ ]:
# Plotting the dataset

def plotMissingValues(dataframe, width, high, character=False):
    plt.figure(figsize=(width, high)) 
    if character==False:
        ax = dataframe.isnull().sum().plot.barh(color='skyblue') 
    else:
        occurrences = (dataframe == character).sum().sort_values(ascending=True)
        ax = occurrences.plot.barh(color='skyblue') 


    # Customizing the plot

    plt.title('Missing Values per Column', fontsize=16)
    plt.xlabel('Number of Missing Values', fontsize=12)
    plt.ylabel('Columns', fontsize=12)
    plt.grid(axis='x', linestyle='--', alpha=0.7) 
    plt.xticks(fontsize=10)
    plt.yticks(fontsize=10)


    # Display the values on the bars
    
    if character==False:
        for i, v in enumerate(dataframe.isnull().sum()):
            ax.text(v + 500, i, str(v), color='gray', va='center', fontsize=8)
    else:
        for i, v in enumerate(occurrences):
            ax.text(v + 500, i, str(v), color='gray', va='center', fontsize=8)

    plt.tight_layout()
    plt.show()

## Import Data (Chunk)

Load the data (one chunk) from a .tsv file

In [ ]:
# Load the data
chunk_size = 100000
chunks_df = pd.read_csv(openfoodfactsUrl, sep="\t", chunksize=chunk_size)

for chunk_df in chunks_df:
    print(chunk_df.shape)
    break

## Data Exploration (Chunk)

Data Exploration...

In [ ]:
# View columns name

print(chunk_df.columns.values)

chunk_df.shape

In [ ]:
# Plotting the dataset
    
plotMissingValues(chunk_df, 7, 30)

## Import Data

Load the data from a .tsv file

In [ ]:
# Create the filter
# $ = keep as is | - = don't keep | ? - keep as optional | t = translate

df_filter = ["code", #$$$$$$
             "product_name", #$$$$$$
             "packaging_tags", #?t?t?t (enumerate)
             "brands", #??????
             "brands_tags", #??????
             "labels_en", #t?t?t? (da processare)
             "countries_en", #$$$$$$ (importare il dataset poi - o countries-tags)
             "ingredients_tags", #$t$t$t (tassonomia - o ingredients_text o ingredients_analysis_tags)
             "serving_size", #??????
             "additives_n", #------ Usato solo per processare additives_tags
             "additives_tags", #?????? (importare il dataset poi)
             "nutriscore_score", #??????
             "nutriscore_grade", #??????
             "nova_group", #??????
             "food_groups", #??????
             "food_groups_tags", #?????? (o food_groups_en)
             "brand_owner", #??????
             "ecoscore_grade", #??????
             #"main_category_en", #------ (sostituito da food_groups_en)
             "energy-kcal_100g", #$$$$$$
             "energy_100g", #$$$$$$
             "fat_100g", #$$$$$$$
             "saturated-fat_100g", #??????
             "trans-fat_100g", #??????
             "cholesterol_100g", #??????
             "carbohydrates_100g", #$$$$$$
             "sugars_100g", #??????
             "fiber_100g", #??????
             "proteins_100g", #$$$$$$
             "salt_100g", #??????
             "sodium_100g", #??????
             "vitamin-a_100g", #??????
             "vitamin-c_100g", #??????
             "calcium_100g", #??????
             "iron_100g"] #??????

In [ ]:
filter_df = pd.read_csv(openfoodfactsUrl, sep="\t", usecols=df_filter)

## Data Exploration

Data Exploration...

In [ ]:
# View columns name

print(filter_df.columns.values)

filter_df.shape

In [ ]:
# Plotting the dataset
    
plotMissingValues(filter_df, 7, 6)

## Data Cleaning

Data Cleaning...

In [ ]:
# Replace null values in additives_tags with empty string if additives_n is 0

def replace_null(row):
    if row['additives_n'] == 0 and pd.isnull(row['additives_tags']):
        return ""
    else:
        return row['additives_tags']
    
def replace_null_bycoll(row, col):
    if pd.isnull(row[col]):
        return ""
    else:
        return row[col]
    

filter_df['additives_tags'] = filter_df.apply(replace_null, axis=1)

filter_df["packaging_tags"] = filter_df.apply(replace_null_bycoll, args=('packaging_tags',), axis=1)
filter_df["brands"] = filter_df.apply(replace_null_bycoll, args=('brands',), axis=1)
filter_df["brands_tags"] = filter_df.apply(replace_null_bycoll, args=('brands_tags',), axis=1)
filter_df["labels_en"] = filter_df.apply(replace_null_bycoll, args=('labels_en',), axis=1)
filter_df["serving_size"] = filter_df.apply(replace_null_bycoll, args=('serving_size',), axis=1)
filter_df["nutriscore_score"] = filter_df.apply(replace_null_bycoll, args=('nutriscore_score',), axis=1)
filter_df["nutriscore_grade"] = filter_df.apply(replace_null_bycoll, args=('nutriscore_grade',), axis=1)
filter_df["nova_group"] = filter_df.apply(replace_null_bycoll, args=('nova_group',), axis=1)
filter_df["food_groups"] = filter_df.apply(replace_null_bycoll, args=('food_groups',), axis=1)
filter_df["food_groups_tags"] = filter_df.apply(replace_null_bycoll, args=('food_groups_tags',), axis=1)
#filter_df["food_groups_en"] = filter_df.apply(replace_null_bycoll, args=('food_groups_en',), axis=1)
filter_df["brand_owner"] = filter_df.apply(replace_null_bycoll, args=('brand_owner',), axis=1)
filter_df["ecoscore_grade"] = filter_df.apply(replace_null_bycoll, args=('ecoscore_grade',), axis=1)
#filter_df["main_category_en"] = filter_df.apply(replace_null_bycoll, args=('main_category_en',), axis=1)
filter_df["saturated-fat_100g"] = filter_df.apply(replace_null_bycoll, args=('saturated-fat_100g',), axis=1)
filter_df["trans-fat_100g"] = filter_df.apply(replace_null_bycoll, args=('trans-fat_100g',), axis=1)
filter_df["cholesterol_100g"] = filter_df.apply(replace_null_bycoll, args=('cholesterol_100g',), axis=1)
filter_df["sugars_100g"] = filter_df.apply(replace_null_bycoll, args=('sugars_100g',), axis=1)
filter_df["fiber_100g"] = filter_df.apply(replace_null_bycoll, args=('fiber_100g',), axis=1)
filter_df["salt_100g"] = filter_df.apply(replace_null_bycoll, args=('salt_100g',), axis=1)
filter_df["sodium_100g"] = filter_df.apply(replace_null_bycoll, args=('sodium_100g',), axis=1)
filter_df["vitamin-a_100g"] = filter_df.apply(replace_null_bycoll, args=('vitamin-a_100g',), axis=1)
filter_df["vitamin-c_100g"] = filter_df.apply(replace_null_bycoll, args=('vitamin-c_100g',), axis=1)
filter_df["calcium_100g"] = filter_df.apply(replace_null_bycoll, args=('calcium_100g',), axis=1)
filter_df["iron_100g"] = filter_df.apply(replace_null_bycoll, args=('iron_100g',), axis=1)

In [ ]:
# Apply the filter to the Dataframe

food_table = filter_df[df_filter].copy()

food_table["isempty"] = np.where(food_table.isnull().sum(axis=1) >= 1, 1, 0)
percentage = food_table.isempty.value_counts()[1] / food_table.shape[0] * 100
print("Percentage of dropped rows: " + str(percentage))

food_table = food_table[food_table.isempty==0].copy()
food_table.isnull().sum()

food_table.drop("isempty", inplace=True,axis=1)
food_table.dropna(axis = 0, how = "any", inplace=True)

In [ ]:
food_table.shape

In [ ]:
# Plotting the dataset
    
plotMissingValues(food_table, 7, 6, character="")

In [ ]:
pd.set_option('display.max_columns', None)
food_table.head()

## Save or Load the Dataset

In [ ]:
# Save the new Dataset

food_table.to_csv(path + '/data/data_2.tsv', sep='\t', index=False)

In [3]:
# Import the Dataset

#food_table = pd.read_csv(foodtableUrl, sep="\t", na_values=['unknown'], keep_default_na=False)
food_table = pd.read_csv(foodtableUrl, sep="\t", na_values='unknown')

E:\Anaconda\lib\site-packages\IPython\core\interactiveshell.py:3146: DtypeWarning: Columns (0) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


## Ingredients Counter

In [ ]:
ingredients_map = {}

def cl_ingredients(text, ingredients_map, debug = False):
    

    # Pattern to split the text
    
    # pattern = r"[,.()\[\]{}]"
    pattern = r"[,]"
    split_text = re.split(pattern, text)

    for ingredient in split_text:
        if ingredient in ingredients_map:
            ingredients_map[ingredient] += 1
        else:
            ingredients_map[ingredient] = 1
    
   
    if debug:
        print(text)
#        print(text)
        
    #return ', '.join(result)

#cl_ingredients(food_table.at[32, 'ingredients_tags'], ingredients_map, False)
food_table['ingredients_tags'].apply(cl_ingredients, args=(ingredients_map,))
print(len(ingredients_map))

In [ ]:
# File path to save the CSV data
file_path = path + '/data/ingrediets_2.tsv'

sorted_ingredients = dict(sorted(ingredients_map.items(), key=lambda x: x[1], reverse=True))

# Writing the dictionary to a CSV file with tab-separated values
with open(file_path, 'w', newline='', encoding='utf-8') as file:
    writer = csv.writer(file, delimiter='\t')
    writer.writerow(['Ingredient', 'Count'])  # Writing header
    for ingredient, count in sorted_ingredients.items():
        writer.writerow([ingredient, count])

print(f"Dictionary has been written to {file_path}")

## Read Taxonomy

In [4]:
def split_line(text):
    
    split_text = re.split(':', text)
    
    language_tag = split_text[0]
    ingredients_text = split_text[1]
    
    ingredients = re.split(', ', ingredients_text)
    stripped_ingredients = [ingredient.strip().lower().replace(" ", "-") for ingredient in ingredients]
    
    return language_tag, stripped_ingredients

def check_synonyms(in_item, synonym_set, stopword_set):
    out = []
    split_in_item = re.split(':', in_item)
    in_tag = split_in_item[0]
    if in_tag in synonym_set:
        for syn_list in synonym_set[in_tag]:
            for syn in syn_list:
                if re.search(f'(^{syn}-)|(-{syn}-)|-{syn}$',split_in_item[1]):
                    for syn2 in syn_list:
                        if syn != syn2:
                            out.append(re.sub(syn, syn2, split_in_item[1]))
            if len(out) != 0:
                break
    if in_tag in stopword_set:
        for stopword in stopword_set[in_tag]:
            if re.search(f'(^{stopword}-)|(-{stopword}-)|-{stopword}$',split_in_item[1]):
                out.append(re.sub('--+', '-', re.sub(stopword, '', split_in_item[1])))
    #if len(out) != 0:
        #print(in_item)
        #print(out)
    return out
                
    
    

In [5]:
#Create synonym and stopword base

def extract_synonyms(file, synonym_set):
    
    cur_line = file.readline()
    while cur_line != '':
        if re.match('^synonyms:[a-z]{2}:', cur_line):
            new_item = re.match('^synonyms:[a-z]{2}:[^#]*', cur_line).group()
            split_item = re.split(':', new_item)
            new_tag = split_item[1]
            new_syns = []
            for word in re.split(',', split_item[2]):
                new_syns.append(word.strip().lower().replace(' ', '-'))
            if '' in new_syns:
                new_syns.remove('')
            if new_tag in synonym_set:
                synonym_set[new_tag].append(new_syns)
            else:
                synonym_set[new_tag] = [new_syns]
        cur_line = file.readline()
    return synonym_set


def extract_stopwords(file, stopword_set):
    
    cur_line = file.readline()
    while cur_line != '':
        if re.match('^stopwords:[a-z]{2}:', cur_line):
            new_item = re.match('^stopwords:[a-z]{2}:[^#]*', cur_line).group()
            split_item = re.split(':', new_item)
            new_tag = split_item[1]
            new_stops = []
            for word in re.split(',', split_item[2]):
                new_stops.append(word.strip().lower().replace(' ', '-'))
            if new_tag not in stopword_set:
                stopword_set[new_tag] = []
            for stop in new_stops:
                stopword_set[new_tag].append(stop)
        cur_line = file.readline()
    for key in stopword_set:
        stopword_set[key] = list(set(stopword_set[key]))
    return stopword_set

synonym_set = {}
stopword_set = {}

with open(ingredients_tx, 'r', encoding='utf-8') as file:
    extract_synonyms(file, synonym_set)
    file.seek(0)
    extract_stopwords(file, stopword_set)
    file.close()

with open(additives_tx, 'r', encoding='utf-8') as file:
    extract_synonyms(file, synonym_set)
    file.seek(0)
    extract_stopwords(file, stopword_set)
    file.close()
    
with open(vitamins_tx, 'r', encoding='utf-8') as file:
    extract_synonyms(file, synonym_set)
    file.seek(0)
    extract_stopwords(file, stopword_set)
    file.close()
    
with open(packaging_materials_tx, 'r', encoding='utf-8') as file:
    extract_synonyms(file, synonym_set)
    file.seek(0)
    extract_stopwords(file, stopword_set)
    file.close()
    
with open(packaging_shapes_tx, 'r', encoding='utf-8') as file:
    extract_synonyms(file, synonym_set)
    file.seek(0)
    extract_stopwords(file, stopword_set)
    file.close()
    
with open(labels_tx, 'r', encoding='utf-8') as file:
    extract_synonyms(file, synonym_set)
    file.seek(0)
    extract_stopwords(file, stopword_set)
    file.close()
    
print(synonym_set)
print(stopword_set)
    

{'en': [['fiber', 'fibre'], ['hydrolysed', 'hydrolyzed'], ['pasteurised', 'pasteurized'], ['wholemeal', 'whole', 'whole-grain', 'wholegrain', 'complete'], ['semi-wholemeal', 'semi-whole', 'semi-whole-grain', 'semi-wholegrain', 'semi-complete', 'semiwhole', 'semiwholemeal'], ['semi-sweet', 'semisweet'], ['fd&c', 'fd-and-c', 'fdc', 'ffdca', 'fdca'], ['n°', 'no', 'number', 'nb'], ['no1', 'n1', '1'], ['no2', 'n2', '2'], ['no3', 'n3', '3'], ['no4', 'n4', '4'], ['no5', 'n5', '5'], ['no6', 'n6', '6'], ['no7', 'n7', '7'], ['no8', 'n8', '8'], ['no9', 'n9', '9'], ['no10', 'n10', '10'], ['no11', 'n11', '11'], ['no12', 'n12', '12'], ['colour', 'color'], ['biobased', 'bio-based', 'biosourced', 'bio-sourced'], ['coloring', 'colouring', 'color', 'colour'], ['flavor', 'flavour', 'flavoring', 'flavouring'], ['gmos', 'genetically-modified-organisms', 'gmo'], ['rich-in', 'high-in'], ['msg', 'glutamate'], ['preservatives', 'conservatives'], ['seafood', 'sea-food'], ['without', '0%', 'free'], ['carbon', 'c

Ingredients

In [ ]:
# Read the taxonomy line by line and add each element to a dictionary

ingredients_tx_map = {}
master = ''
master_tag = ''
start = True
count_masters = 0

with open(ingredients_tx, 'r', encoding='utf-8') as file:
    
    for line in file:
        
        # Iterate until ingredients
        if start and '# # # # # # # # # # # # # #' not in line:
            continue
        else:
            start = False
            
        # Check if there is a new section
        if line == '\n':
            master = ''
            #print('reset')
            
        # Skip the line if is a comment or if is not a valid line
        if '#' in line or line.count(':') != 1 or '<' in line:
            continue
        
        language_tag, ingredients = split_line(line)
        
        # Add the line to the dictionary
        if language_tag == 'en' or master == '':
            master = ingredients[0]
            master_tag = language_tag
            count_masters += 1
        
        for ingredient in ingredients:
            ingredient = ingredient
            ingredients_tx_map[language_tag+':'+ingredient] = master_tag+':'+master
        
        
    print('# of elements in the dictionary: ' + str(len(ingredients_tx_map)))
    print('# of master elements in the dictionary: ' + str(count_masters) + '\n')
    print(ingredients_tx_map)

In [6]:
ing_dict = {}

with open(ingredients_tx, 'r', encoding='utf-8') as file:
    
    cur_line = file.readline()
    while cur_line != '':
        cur_ing = ''
        super_items = []
        if re.match('^<?[a-z]{2}:', cur_line):
            while re.match('^<[a-z]{2}:', cur_line):
                new_item = re.match('^<[a-z]{2}:[^#]*', cur_line).group()
                new_item = re.split(':', new_item)[1]
                super_items.append(re.sub('"', "'", re.sub('--+', '-', new_item.strip().lower().replace(' ', '-'))))
                cur_line = file.readline()
            while cur_line != '\n' and cur_line != '':
                if re.match('^[a-z]{2}:', cur_line):
                    new_item = re.match('^[a-z]{2}:[^#]*', cur_line).group()
                    new_item = re.split(':', new_item)
                    new_tag = new_item[0]
                    new_items = re.split(',', new_item[1])
                    for item in new_items:
                        item = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                    if cur_ing == '':
                        cur_ing = re.sub('"', "'", re.sub('--+', '-', new_items[0].strip().lower().replace(' ', '-')))
                        ing_dict[cur_ing] = [super_items,[]]
                    for item in new_items:
                        f_name = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                        f_item = f"{new_tag}:{f_name}"
                        ing_dict[cur_ing][1].append(f_item)
                        for synoym in check_synonyms(f_item, synonym_set, stopword_set):
                            ing_dict[cur_ing][1].append(f"{new_tag}:{synoym}")
                cur_line = file.readline()
            if(cur_ing != ''):
                ing_dict[cur_ing][1] = list(set(ing_dict[cur_ing][1]))
                print(cur_ing + f":\n{ing_dict[cur_ing]}\n")
        cur_line = file.readline()
    file.close()

imazalil:
[[], ['en:imazalil', 'sk:imazalil', 'es:imazalil', 'pl:imazalil', 'pt:imazalil', 'fa:انیل\u200cکونازول', 'hu:imazalil', 'it:imazalil', 'da:imazalil', 'ja:イマザリル', 'fr:imazalil', 'nl:imazalil', 'de:imazalil', 'sl:imazalil', 'fi:imatsaliili']]

frying:
[[], ['fr:friture', 'en:frying']]

caramel-syrup:
[[], ['hr:karamelov-sirup', 'lt:karamelizuoto-sirupo', 'en:caramel-syrup', 'it:sciroppo-di-caramello', 'ja:キャラメルシロップ', 'de:karamellsirup', 'hu:karamellszirup', 'fi:karamellisiirappi', 'bg:карамелен-сироп', 'es:sirope-de-caramelo', 'ru:карамельный-сироп', 'ca:xarop-de-carmel', 'es:jarabe-caramelo', 'es:sirope-caramelo', 'pt:xarope-de-caramelo', 'ca:caramel-liquid', 'es:jarabe-de-caramelo', 'lt:karamelizuotas-sirupas', 'pl:syrop-karmelowy', 'ja:カラメルシラップ', 'fr:sirop-de-caramel', 'pt:xarope-caramelo', 'hu:karamella-szirup', 'da:karamelsukkersirup', 'de:caramelsirup', 'ca:xarop-carmel', 'fr:sirop-caramel', 'es:caramelo-líquido', 'hu:karamell-szirup', 'hr:karamelizirani-sirup', 'hr:karam

sunflower-lecithin:
[['e322(i)'], ['lt:lecitinai-iš-saulėgrąžų', 'lt:lecitinai-saulėgrąžų', 'de:sonnenblumenlecithin', 'lv:saulespuku-lecitīns', 'ca:lecitines-gira-sol', 'hu:napraforgó-lecitin', 'da:solsikkelecithin', 'it:lecitine-di-girasole', 'lt:emulsiklis-lecitinai-(saulėgrąžų)', 'sk:slnečnicový-lecitín', 'lv:saulespuķu-lecitīns', 'de:sonnenblumenlecithine', 'sv:solroslecithin', 'et:päevalilleletsitiin', 'ru:лецитин-подсолнечный', 'lv:lecitinai-iš-saulègrąžų', 'ca:lecitines-de-gira-sol', 'es:lecitina-girasol', 'it:lecitina-di-girasole', 'et:päevalille-letsitiin', 'fr:lécithine-tournesol', 'bg:слънчогледов-лецитин', 'lv:saulespuķu-lecitīni', 'pl:lecytyny-ze-słonecznika', 'hr:suncokretov-lecitin', 'es:lecitinas-de-girasol', 'es:lecitinas-girasol', 'nb:solsikkelecithin', 'pl:lecytyny-słonecznikowe', 'nb:solsikkelecitin', 'pt:lecitina-girassol', 'sv:solroslecitin', 'nn:solsikkelecithin', 'pt:lecitina-de-girassol', 'pl:lecytyna-słonecznikowa', 'el:λεκιθίνες-ηλιστροπιου', 'ca:lecitina-de

mono-and-diglycerides-of-fatty-acids-of-vegetable-origin:
[['e471'], ['pt:mono-diglicéridos-d-ácidos-gordos-d-origm-vgtal', 'es:monoglicéridos-y-diglicéridos-de-ácidos-grasos-de-vegetal', "ca:diglicèrids-d'àcids-grassos-d'origen-vegetal", 'pt:mono-e-diglicéridos-de-ácidos-graxo-de-origem-vegetal', "fr:mono-diglycérides-d'acides-gras-d'origine-végétale", "fr:mono-et-diglycérides-d'acides-matières-grasses-d'origine-végétale", 'en:mono-and-diglycerides-of-fatty-acids-of-vegetable-origin', 'es:monoglicéridos-y-diglicéridos-ácidos-grasos-origen-vegetal', 'es:diglicéridos-de-ácidos-grasos-de-origen-vegetal', 'de:mono-und-diglyzeride-speisefettsäuren', 'es:monoglicéridos-y-diglicéridos-de-ácidos-grasos-de-origen-vegetal', "fr:mono-et-diglycérides-d'acides-mg-d'origine-végétale", "ca:monoglicèrids-d'àcids-grassos-d'origen-vegetal", 'es:diglicéridos-ácidos-grasos-origen-vegetal', 'pt:mono-e-diglicéridos-ácidos-gordos-origem-vegetal', 'en:mono-and-diglycerides-fatty-acids-vegetable-origin', 'pt:

corn-dextrin:
[['e1400'], ['es:xtrina-maiz', 'fi:maissidekstriini', 'fr:dextrine-de-maïs', 'hu:dextrin-kukoricából', 'en:corn-dextrin', 'es:dextrina-de-maiz', 'it:destrina-di-mais', 'fr:xtrine-maïs', 'bg:царевичен-декстрин', 'nl:maïsdextrine', 'de:maisdextrin', 'hu:kukoricadextrin']]

modified-potato-starch:
[['modified-starch', 'potato-starch'], ['ca:midó-modificat-de-patata', 'en:modified-potato-starch', 'pt:amido-batata-modificado', 'fr:amidon-de-pomme-de-terre-modifié', 'es:almidon-de-patata-modificado', 'ja:じゃがいもでん粉', 'pt:amido-de-batata-modificado', 'es:almidón-modificado-de-patata', 'fr:fécule-modifiée-pommes-terre', 'fr:amidon-modifié-de-pommes-de-terre', 'de:modifizierte-kartoffelstärke', 'pl:skrobia-modyfikowana-ziemniaczana', 'fr:amidon-transformé-de-pomme-de-terre', 'hu:módosított-burgonyakeményítő', 'es:almidón-modificado-patata', 'fr:fécule-pomme-terre-modifiée', 'nl:gemodificeerd-aardappelzetmeel', 'fr:amidon-modifié-pomme-terre', 'hr:modificirani-krumpirov-škrob', 'fr:a

sourdough-starter:
[['lactic-ferments'], ['da:surdejskultur', 'de:sauerteigstarterkulturen', 'es:levadura-de-origen-natural-de-masa-madre', 'es:levadura-masa-madre', 'en:sourdough-culture', 'es:levadura-origen-natural-de-masa-madre', 'de:sauerteigkulturen', 'de:sauerteig-starter', 'es:levadura-natural-masa-madre', 'fr:starters-pour-levain', 'en:sourdough-starter', 'de:sauerteigstarter', 'es:levadura-natural-de-masa-madre', 'es:levadura-de-masa-madre']]

vegan-lactic-ferments:
[['lactic-ferments'], ['sv:vegansk-yoghurtkultur', 'fr:cultures-lactiques-véganes', 'en:vegan-lactic-ferments', 'da:vegansk-yoghurtkultur', 'es:fermentos-lácticos-veganos', 'de:vegane-joghurtkulturen', 'nb:vegansk-yoghurtkultur']]

lactic-and-aging-ferments:
[['lactic-ferments'], ["it:fermenti-lattici-e-d'affinatura", 'it:fermenti-lattici-e-invecchianti', 'pt:fermentos-lácticos-e-de-maturação', 'de:milch-alterungsfermente', 'es:fermentos-lácticos-y-maduración', 'en:lactic-and-aging-ferments', "fr:ferment-lactique-

...

broth:
[[], ['li:boeljóng', 'fr:fond-sauce', 'de:bouillons', "uz:sho'rva", 'nb:buljong', 'ja:だし', 'hi:यखनी', 'ca:brou', 'ko:브로스', 'zh:清汤', 'hr:bujon', 'ro:supă', 'sq:supë', 'pa:ਸ਼ੋਰਬਾ', 'fa:گوشتابه', 'nl:bouillon', 'az:bulyon', 'ja:ブイヨン', 'mk:бујо́н', 'is:seyði', 'pl:wywar', 'fr:bouillon', 'hy:արգանակ', 'mt:brodu', 'pt:caldo', 'el:ζωμός', 'fi:liemivalmiste', 'ru:бульон', 'gl:caldo', 'af:bouillon', 'ba:һурпа', 'ja:出汁', 'de:brühen', 'uk:бульйон', 'es:caldo', 'bn:সুরুয়া', 'io:buliono', 'de:brühe', 'lt:sultinys', 'tl:tsaa-ng-karneng-baka', 'fr:fond', 'nl:bouillons', 'id:kaldu', 'ms:kaldu', 'da:fond', 'ar:زومات', 'en:stock', 'bg:бульон', 'cs:vývar', 'gd:brot', 'pl:bulion', 'eo:buljono', 'da:bouillon', 'sv:buljongpreparat', 'tr:etsuyu', 'en:fond', 'he:ציר', 'et:puljong', 'yi:יויך', 'sv:buljong', 'fr:fond-de-sauce', 'hu:húsleves', 'es:caldos', 'ia:bouillon', 'lb:britt', 'be:булён', 'en:stocks', 'it:brodo', 'nn:buljong', 'en:broths', 'ga:anraith', 'eu:salda', 'vi:canh', 'en:broth', 'fi:liemi'

black-pudding:
[['meat'], ['de:black-pudding', 'en:black-pudding', 'ca:baldana', 'es:morcilla']]

viande-cuisinée:
[[], ['fr:viande-cuisinée']]

ice-cream:
[[], ['la:glacies-edibilis', 'hr:sladoled', 'ro:înghețată', 'el:παγωτό', 'hy:պաղպաղակ', 'gu:આઇસ્ક્રીમ', 'bs:sladoled', 'cy:hufen-iâ', 'de:speiseeis', 'sq:akullorja', 'bg:сладолед', 'de:eiskrem', 'nn:iskrem', 'si:අයිස්-ක්\u200dරීම්', 'vi:kem-lạnh', 'ms:aiskrim', 'se:lákcajiekŋa', 'sk:zmrzlina', 'be:марожанае', 'ia:gelato', 'zu:u-ayisikhilimu', 'ab:аршәы', 'pt:gelado', 'uk:морозиво', 'nv:abeʼ-yistiní', 'nb:iskrem', 'cs:zmrzlina', 'he:גלידה', 'ka:ნაყინი', 'gv:key-riojey', 'te:ఐస్-క్రీం', 'tg:яхмос', 'ru:мороженое', 'eo:glaciaĵo', 'af:roomys', 'rm:glatsch', 'hu:jégkrémek', 'tk:dongdurma', 'ca:gelats', 'ku:bestenî', 'fy:rjemme-iis', 'mk:сладолед', 'pa:ਆਈਸ-ਕਰੀਮ', 'ar:مثلجات', 'tt:туңдырма', 'br:dienn-skorn', 'ur:آئس-کریم', 'ca:gelat', 'sl:sladoled', 'gd:reòiteag', 'wo:galaas', 'ml:ഐസ്\u200cക്രീം', 'my:ရေခဲမုန့်', 'et:jäätis', 'ga:uachtar

harissa:
[['sauce'], ['en:harissa', 'zh:哈里薩辣醬', 'ur:ھریسا', 'ko:하리사', 'fa:هریسه', 'en:harissa-paste', 'hy:հարիսա', 'pl:harissa', 'ar:هريسة', 'hi:हरीसा', 'eo:hariso', 'bn:হরিষ্যা', 'ka:ჰარისა', 'bg:хариса', 'sr:harisa', 'xx:harissa', 'he:אריסה', 'ja:ハリッサ', 'la:erise', 'ru:харисса', 'pa:ਹਰੀਸਾ']]

prepacked-harissa:
[['harissa'], ['fr:sauce-condimentaire-harissa', 'en:prepacked-harissa']]

espagnole-sauce:
[['sauce'], ['fa:سس-اسپانیول', 'ca:salsa-espanyola', 'id:saus-espagnole', 'fi:sauce-espagnole', 'de:spanische-sauce', 'es:salsa-española', 'uk:еспаньйол', 'pt:molho-espanhol', 'tr:espagnole-sosu', 'ru:эспаньоль', 'he:רוטב-אספניול', 'en:espagnole-sauce', 'it:salsa-spagnola', 'zh:棕醬', 'sv:espagnole', 'de:sauce-espagnole', 'ms:sos-espagnole', 'ja:エスパニョールソース', 'fr:sauce-espagnole']]

ketchup:
[['sauce'], ['sl:kečap', 'es:tomate-ketchup', 'sd:ڪيچپ', 'sv:ketchup', 'fi:mausteketsuppi', 'uk:кетчуп', 'ar:كتشب', 'pl:keczup', 'sr:кечап', 'yi:קעטשאפ', 'lv:kečups', 'ko:케첩', 'de:ketchup', 'en:ketchup

remoulade-sauce:
[['sauce'], ['ko:레물라드', 'en:remoulade', 'eo:remolado', 'pl:remulada', 'oc:remolada', 'de:remoulade', 'he:רמול', 'io:remulado', 'ru:ремулад', 'da:remoulade', 'et:remoulade', 'de:remouladensauce', 'fr:sauce-rémoulade', 'cs:remuláda', 'en:remoulade-sauce', 'sv:remouladsås', 'bn:রিম্যোলেড', 'fi:remoulade', 'ja:レムラード・ソース', 'nb:remulade', 'ca:remolada', 'bg:ремулада', 'es:remoulade', 'nl:remouladesaus', 'nl:remoulade', 'pa:ਰੇਮੂਲਾਦ']]

sweet-and-sour-sauce:
[['sauce'], ['nl:zoetzure-saus', 'nb:sursøt-saus', 'fi:hapanimeläkastike', 'fr:sauce-aigre-douce', 'it:salsa-agrodolce', 'bg:сладко-кисел-сос', 'de:susssäure-sauce', 'eo:dolĉacida-saŭco', 'en:sweet-and-sour-sauce', 'ko:탕추', 'es:salsa-agridulce', 'is:súrsæt-sósa', 'pt:molho-agridoce', 'uk:кисло-солодкий-соус', 'he:רוטב-חמוץ-מתוק', 'ja:糖酢醤', 'id:saus-asam-manis', 'sv:sötsur-sås', 'pl:sos-słodko-kwaśny']]

teriyaki-sauce:
[['sauce'], ['de:teriyaki-soße', 'bg:сос-терияки', 'nl:teriyakisaus', 'en:teriyaki-sauce', 'fr:sauce-teri

vegetable-margarine:
[['margarine'], ['bg:растителен-маргарин', 'de:pflanzenmargarine', 'de:pflanzliche-margarine', 'fr:margarine-végétale', 'da:vegetabiliskt-margarin', 'nn:vegetabiliskt-margarin', 'sv:vegetabiliskt-margarin', 'nl:plantaardige-margarine', 'en:vegetable-margarine', 'fi:kasvimargariini', 'it:margarina-vegetale', 'pt:margarina-vegetal', 'sk:rastlinný-margarín', 'cs:rostlinný-margarín', 'es:margarina-vegetal', 'fi:kasvismargariini', 'en:vegetal-margarine', 'pl:margaryna-roślinna']]

solid-vegetable-fat-for-frying:
[['vegetable-margarine'], ['en:solid-vegetable-fats-for-frying', 'fr:matière-grasse-graisse-végétale-solide-pr-friture', 'en:solid-vegetable-fat-for-frying', 'fr:matière-grasse-ou-graisse-végétale-solide-pour-friture']]

50-63%-unsalted-vegetable-fat-high-in-omega-3:
[['vegetable-margarine'], ['fr:matière-grasse-végétale-allégée-à-50-63%-riche-en-oméga-3', 'en:50-6no3%-unsalted-vegetable-fat-high-in-omega-no3', 'fr:matière-grasse-végétale-allégée-à-50-63%-fort-e

In [7]:
add_dict = {}

with open(additives_tx, 'r', encoding='utf-8') as file:
    
    cur_line = file.readline()
    while cur_line != '':
        cur_add = ''
        super_items = []
        if re.match('^<?[a-z]{2}:', cur_line):
            while re.match('^<[a-z]{2}:', cur_line):
                new_item = re.match('^<[a-z]{2}:[^#]*', cur_line).group()
                new_item = re.split(':', new_item)[1]
                super_items.append(re.sub('"', "'", re.sub('--+', '-', new_item.strip().lower().replace(' ', '-'))))
                cur_line = file.readline()
            while cur_line != '\n' and cur_line != '':
                if re.match('^[a-z]{2}:', cur_line):
                    new_item = re.match('^[a-z]{2}:[^#]*', cur_line).group()
                    new_item = re.split(':', new_item)
                    new_tag = new_item[0]
                    new_items = re.split(',', new_item[1])
                    for item in new_items:
                        item = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                    if cur_add == '':
                        cur_add = re.sub('"', "'", re.sub('--+', '-', new_items[0].strip().lower().replace(' ', '-')))
                        add_dict[cur_add] = [super_items,[]]
                    for item in new_items:
                        f_name = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                        f_item = f"{new_tag}:{f_name}"
                        add_dict[cur_add][1].append(f_item)
                        for synoym in check_synonyms(f_item, synonym_set, stopword_set):
                            add_dict[cur_add][1].append(f"{new_tag}:{synoym}")
                cur_line = file.readline()
            if(cur_add != ''):
                add_dict[cur_add][1] = list(set(add_dict[cur_add][1]))
                print(cur_add + f":\n{add_dict[cur_add]}\n")
        cur_line = file.readline()
    file.close()

e100:
[[], ['en:curcumin', 'nb:e100', 'fr:e100', 'hr:curcumin', 'ca:e100', 'de:kurkumaextrakt', 'nl:kurkuma-extract', 'th:e100', 'es:e100', 'ro:curcumină', 'de:kurkumin', 'hu:e100', 'bs:e100', 'fa:کورکومین', 'hr:kurkumin', 'el:e100', 'lv:kurkumīns', 'pl:ekstrakt-z-kurkumy', 'cs:e100', 'zh:e100', 'es:curcumina', 'ja:クルクミン', 'pl:kurkumina', 'fr:extrait-curcuma', 'da:gurkemejeekstrakt', 'fi:kurkumiini', 'da:curcumin', 'de:e100', 'ro:e100', 'sk:kurkumín', 'id:e100', 'tr:e100', 'sv:kurkumin', 'lt:kurkuminas', 'ru:куркумины', 'fr:extrait-de-curcuma', 'hr:e100', 'pt:curcumina', 'fa:e100', 'es:extracto-cúrcuma', 'lv:e100', 'ca:curcumina', 'fi:kurkumiinia', 'mt:e100', 'bs:kurkumin', 'vi:e100', 'pl:ekstrakt-kurkumy', 'en:turmeric-extract', 'nb:kurkumin', 'hr:ekstrakt-kurkume', 'cs:kurkumin', 'et:kurkumiin', 'pl:e100', 'ar:e100', 'lt:e100', 'it:curcumina', 'mt:kurkumina', 'pl:barwiący-wyciąg-kurkumy', 'bg:куркумин', 'he:e100', 'es:extracto-de-cúrcuma', 'kn:e100', 'ja:e100', 'uk:e100', 'pt:e100', 

e104:
[[], ['es:amarillo-de-quinoleína', 'cs:e-104', 'ca:groc-de-quinoleina', 'ca:groc-quinoleina', 'cs:chinolinová-žluť-ws', 'it:e104', 'fr:ci-47005', 'pl:żółcień-chinolinowa', 'mt:e104', 'fr:jaune-quinoléine', 'de:e-104', 'nl:e104', 'cs:chinolinová-žluť', 'da:e104', 'hu:e104', 'nl:chinolinegeel', 'cs:e104', 'en:e104', 'mt:isfar-tal-kinolin', 'da:quinolingult', 'pt:amarelo-quinoleína', 'sl:e104', 'fi:kinoliinikeltainen-ws', 'sv:kinolingult', 'et:e104', 'nl:chinoline-geel', 'ca:e104', 'ca:groc-quinoleína', 'sl:kinolinsko-rumeno', 'it:giallo-chinolina', 'es:e-104', 'lt:chinolino-geltonasis', 'cs:cl-47005', 'en:food-yellow-13', 'de:e104', 'fr:jaune-de-quinoléine', 'ro:galben-de-chinolină', 'lv:e104', 'fi:e104', 'sk:chinolínová-žltá', 'lv:hinolīna-dzeltenais', 'ro:e104', 'fi:ci-47005', 'bg:e104', 'es:amarillo-quinolina', 'de:chinolingelb', 'bg:хинолин-жълто', 'pt:amarelo-de-quinoleína', 'el:e104', 'es:e104', 'el:κιτρινο-κινολινης', 'pl:e104', 'sv:e104', 'ca:groc-de-quinoleína', 'en:quinol

e122:
[[], ['pt:carmosina', 'cs:carmoisin', 'sk:azorubín', 'fr:ci-14720', 'es:c.i.-14720', 'fi:e122', 'es:azorubina-s', 'en:brillantcarmoisin-o', 'da:e-122', 'et:e122', 'hu:karmazsin', 'fi:azorubine', 'en:azorubin-s', 'nl:e122', 'fr:e-122', 'da:carmoisin', 'et:asorubiin', 'el:αζωρουμπινη', 'sv:azorubin', 'cs:e-122', 'en:e122', 'bg:кармоизин', 'mt:ażorubina', 'fr:3567-69-9', 'lt:karmuazinas', 'it:azorubina', 'nl:ci-14720', 'bg:азорубин', 'fr:azorubine-carmoisine', 'lt:e122', 'en:c.i.-14720', 'ca:azorrubina', 'es:brillantcarmoisin-o', 'sl:e122', 'nl:azorubine', 'sv:e-122', 'fi:karmosiini', 'fr:azorubine', 'sk:karmoizín', 'sv:karmosin', 'nl:karmozijn', 'sv:e122', 'fi:karmosiinia', 'pl:e122', 'de:azorubin', 'cs:karmoisin', 'hu:e122', 'es:e122', 'en:food-red-no3', 'es:acid-red-14', 'es:carmisina', 'en:carmoisine', 'xx:e122', 'fi:carmoisine', 'lv:e122', 'et:karmoisiin', 'mt:e122', 'en:azorubine', 'cs:azorubín', 'pt:azorrubina', 'ca:e122', 'fi:ci-14720', 'en:food-red-3', 'lv:karmoizīns', 'fr:

e128:
[[], ['fr:ci-food-red-10', 'fi:dinatrium-5-asetamido-4-okso-3-(fenyylihydratsinyylideeni)naftaleeni-2\\', 'fr:d&c-red-11', 'fr:azofloxin', 'es:e128', 'bg:e128', 'lt:e128-food-additive', 'bg:e128-food-additive', 'el:e128', 'fi:atsogeraniini', 'fr:acid-red-1', 'fi:ci-18050', 'sl:e128-food-additive', 'ca:e128', 'sv:e-128', 'xx:e128', 'fi:e128', 'fi:punainen-2g', 'fr:e128', 'fr:cas-3734-67-6', 'fr:azo-geranine-2g', 'de:e128', 'it:e128-food-additive', 'fr:amidonaphthol-red-g', 'fr:c.i.-18050', 'ro:e128', 'sv:e128', 'en:e128', 'fr:azophloxine', 'fr:ci-acid-red-1', 'hu:e128', 'es:rojo-2g', 'et:e128', 'pt:e128-vermelho-2g', 'mt:e128', 'sv:röd-2g', 'de:red-2g', 'hu:red-2g', 'cs:e128-food-additive', 'fr:red-2g', 'de:rot-2g', 'pl:e128', 'et:e128-food-additive', 'pt:e128', 'ro:roșu-2g', 'en:red-2g', 'ca:vermell-2g', 'de:roth-2g', 'da:e128-food-additive', 'sk:e128', 'lv:e128', 'lv:e128-food-additive', 'nl:ci-18050', 'fr:ci-no.-18050', 'cs:e128', 'pt:vermelho-2g', 'it:e128', 'nl:rood-2g', 'lt:

e140(i):
[['e140'], ['hu:klorofillok', 'pl:ci-zieleń-naturalna-3', 'sr:e140(i)', 'fr:phéophytine-magnésium', 'gl:e140(i)', 'fr:chlorophylles-magnésium', 'gu:હરિતદ્રવ્ય', 'hu:ci-natural-green-3', 'jv:klorofil', 'ta:e140(i)', 'io:klorofilo', 'lv:hlorofili', 'nl:e140(i)', 'pt:verde-origem-natural-ci-3', 'ky:хлорофилл', 'hr:e140(i)', 'jv:e140(i)', 'el:χλωροφυλλες', 'ta:பச்சையம்', 'en:chlorophyll', 'kk:хлорофилл', 'sh:hlorofil', 'uk:хлорофіл', 'mt:ci-natural-green-3', 'th:คลอโรฟิลล์', 'it:e140(i)', 'sv:magnesiumklorofyll', 'sv:klorofyller', 'oc:clorofilla', 'ba:e140(i)', 'fr:vert-naturel-c.-i.-no-3', 'ko:e140(i)', 'en:ci-natural-green-no3', 'ga:clóraifill', 'pl:chlorofile', 'eo:klorofilo', 'fr:phéophytine-au-magnésium', 'hu:e140(i)', 'de:chlorophylle', 'ar:e140(i)', 'da:chlorophyll', 'kn:e140(i)', 'mt:manjeżju-klorofill', 'fr:vert-naturel-ci-n°3', 'ms:e140(i)', 'te:e140(i)', 'es:ci-origen-natural-green-3', 'gl:clorofila', 'sv:e140(i)', 'he:כלורופיל', 'sh:e140(i)', 'cs:chlorofyly', 'sk:chlor

...


e1204:
[[], ['fi:pullulaania', 'it:glucano-lineare', 'pt:neutro', 'pt:e1204', 'en:linear', 'sl:pululan', 'pl:e1204', 'de:e1204', 'mt:pullulan', 'pl:pullulan', 'sk:lineárny', 'sv:e1204', 'sv:pullulan', 'lt:e1204', 'fi:neutraalia-glukaania', 'cs:pullulan', 'fr:9057-02-7', 'fr:pullulane', 'nl:onvertakt', 'it:pullulano', 'fr:e1204', 'lv:pullulāns', 'en:pullulan', 'bg:пулулан', 'mt:glukan-lineari', 'ro:neutru', 'de:pullulan', 'fi:lineaarinen', 'nl:e1204', 'et:e1204', 'lv:e1204', 'sk:e1204', 'sk:pululán', 'el:e1204', 'es:pululano', 'es:e1204', 'en:e1204', 'da:lineær', 'ro:pululan', 'ca:e1204', 'cs:lineární', 'sv:rak', 'bg:e1204', 'nl:neutraal-glucan', 'lt:pululanas', 'et:pullulaan', 'sl:e1204', 'fr:(c37h62o30)n', 'da:pullulan', 'de:e-1204', 'pt:glucano-linear', 'hu:e1204', 'xx:e1204', 'pt:pululana', 'fi:e1204', 'el:γραμμική', 'mt:e1204', 'da:e1204', 'ca:pullulan', 'fr:pullulan', 'hu:pullulán', 'it:e1204', 'da:neutral-glucan', 'cs:e1204', 'fi:neutraali-glukaani', 'nl:pullulan', 'ro:e1204', '

e1410:
[[], ['et:monotärklisfosfaat', 'fi:monotärkkelysfosfaattia', 'sl:monoškrobni-fosfat', 'sl:e1410', 'cs:e1410', 'de:e1410', 'hu:e1410', 'en:monostarch-phosphate', 'es:fosfato-monoalmidón', 'fi:monotärkkelysfosfaatti', 'ca:fosfat-monomidó', 'sv:monostärkelsefosfat', 'pt:fosfato-de-monoamido', 'et:e1410', 'el:e1410', 'bg:мононишестен-фосфат', 'mt:e1410', 'da:monostivelsephosphat', 'lv:e1410', 'xx:e1410', 'ro:e1410', 'sk:e1410', "fr:phosphate-d'amidon", 'pt:fosfato-monoamido', 'hu:monokeményítő-foszfát', 'pt:e1410', 'ro:fosfat-de-amidon', 'nl:e1410', 'sv:e1410', 'bg:e1410', 'fi:e1410', 'el:δισοξινο-φωσφορικο-αμυλο', 'es:e1410', 'ca:fosfat-de-monomidó', 'it:fosfato-di-monoamido', 'lt:monokrakmolo-fosfatas', 'cs:fosforečnan-škrobu', 'en:e1410', 'da:e1410', 'fr:e1410', 'lt:e1410', 'ca:fosfat-monomido', 'sl:monoškrobni-fosfat-je-škrob', 'nl:monozetmeelfosfaat', 'es:fosfato-de-monoalmidón', 'pl:e1410', 'pl:fosforan-monoskrobiowy', 'de:monostärkephosphat', 'mt:fosfat-monoammidiku', 'ca:e14

e1423:
[[], ['fr:glycérol-acétylé-de-diamidon', 'de:acetyliertes-distärkeglycerin', 'fr:e1423', 'fi:asetyloitu-ditärkkelysglyseroli', 'sk:e1423', 'sv:e1423', 'el:e1423', 'lv:e1423-food-additive', 'mt:e1423-food-additive', 'pl:e1423', 'hu:e1423-food-additive', 'it:e1423-food-additive', 'sl:e1423-food-additive', 'xx:e1423', 'bg:e1423', 'cs:e1423', 'es:glicerol-dialmidón-acetilado', 'ro:e1423', 'fr:glycérol-de-diamidon-acétylé', 'fi:asetyloitua-ditärkkelysglyserolia', 'lv:e1423', 'pt:e1423', 'cs:e1423-food-additive', 'fr:glycérol-acétylé-diamidon', 'da:e1423', 'es:e1423', 'de:e1423', 'sv:e1423-food-additive', 'pt:e1423-food-additive', 'da:e1423-food-additive', 'hu:e1423', 'nl:geacetyleerd-dizetmeelglycerol', 'bg:e1423-food-additive', 'it:e1423', 'fi:e1423', 'mt:e1423', 'et:e1423-food-additive', 'sl:e1423', 'es:glicerol-de-dialmidón-acetilado', 'lt:e1423', 'el:e1423-food-additive', 'lt:e1423-food-additive', 'sk:acetylovaný-škrobový-glycerol', 'et:e1423', 'nl:e1423', 'ro:e1423-food-additive

e1452:
[[], ['pl:sól-glinowa-oktenylobursztynianu-skrobiowego', 'lt:krakmolo-aliuminio-oktenilsukcinatas', 'el:e1452', 'de:e1452', 'cs:škrobový-oktenylsukcinát-hlinitý', 'sv:stärkelse-aluminium-oktenyl-succinat', 'sv:e1452', 'da:stivelsealuminiumoctenylsuccinat', 'fi:e1452', 'de:stärkealuminiumoctenylsuccinat', 'cs:e1452', 'hu:e1452', 'sl:e1452', 'sl:aluminijev-oktenil-sukcinat-škroba', 'bg:скорбелен-алуминиев-октенил-сукцинат', 'fi:tärkkelysalumiinioktenyylisukkinaatti', 'it:e1452', 'et:e1452', 'lt:e1452', 'xx:e1452', 'fi:tärkkelysalumiinioktenyylisukkinaattia', 'en:e1452', 'sk:škrobový-oktenyljantaran-hlinitý', 'pt:octenilsuccinato-de-amido-alumínico', 'pt:e1452', 'nl:zetmeelaluminiumoctenylsuccinaat', 'ca:octenilsuccinat-alumínic-midó', 'es:octenilsuccinato-alumínico-de-almidón', 'hu:keményítő-alumínium-oktenil-szukcinát', 'sk:e1452', 'ca:octenilsuccinat-alumínic-de-midó', "fr:octénylesuccinate-d'amidon-et-d'aluminium", 'pl:e1452', 'es:e1452', 'it:ottenilsuccinato-di-alluminio-e-ami

e1518:
[[], ['fr:2\\', 'it:c9h14o6', 'fr:c9h14o6', 'en:glycerin-triacetate', 'es:triacetín', 'bg:глицерил-триацетат', 'et:e1518', 'ca:triacetina', 'bg:e1518', 'hr:gliceril-triacetat', 'nl:glyceroltriacetaat', 'sv:e1518', 'en:3-triacetoxypropane', 'nl:e1518', 'pt:triacetato-de-glicerilo', 'et:glütserüültriatsetaat', 'da:glyceryltriacetat', 'en:2\\', 'it:e1518', 'pl:e1518', 'lt:gliceriltriacetatas', 'cs:glycerolester-kyseliny-octové', 'fr:triacétate-glycéryle', 'xx:e1518', 'de:3-propantriol-triacetat', 'fi:glyserolitriasetaattia', 'de:triacetin', 'de:e1518', 'de:3-triacetoxypropan', 'fr:triacétate-glycérine', 'it:triacetato-di-glicerile', 'da:e1518', 'cs:glyceryl-triacetát', 'fr:102-76-1', 'fr:3-triacétoxypropane', 'en:e1518', 'en:n3-triacetoxypropane', 'de:triessigsäureglycerinester', 'el:τριακετινη-(τριγλυκεριδιο-του-οξικου-οξεος)', 'en:triacetin', 'lv:glicerīna-triacetāts', 'fr:e1518', 'de:e-1518', 'sk:e1518', 'pt:triacetato-glicerilo', 'en:no3-triacetoxypropane', 'hu:e1518', 'ro:e151

In [8]:
vit_dict = {}

with open(vitamins_tx, 'r', encoding='utf-8') as file:
    
    cur_line = file.readline()
    while cur_line != '':
        cur_vit = ''
        super_items = []
        if re.match('^<?[a-z]{2}:', cur_line):
            while re.match('^<[a-z]{2}:', cur_line):
                new_item = re.match('^<[a-z]{2}:[^#]*', cur_line).group()
                new_item = re.split(':', new_item)[1]
                super_items.append(re.sub('"', "'", re.sub('--+', '-', new_item.strip().lower().replace(' ', '-'))))
                cur_line = file.readline()
            while cur_line != '\n' and cur_line != '':
                if re.match('^[a-z]{2}:', cur_line):
                    new_item = re.match('^[a-z]{2}:[^#]*', cur_line).group()
                    new_item = re.split(':', new_item)
                    new_tag = new_item[0]
                    new_items = re.split(',', new_item[1])
                    for item in new_items:
                        item = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                    if cur_vit == '':
                        cur_vit = re.sub('"', "'", re.sub('--+', '-', new_items[0].strip().lower().replace(' ', '-')))
                        vit_dict[cur_vit] = [super_items,[]]
                    for item in new_items:
                        f_name = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                        f_item = f"{new_tag}:{f_name}"
                        vit_dict[cur_vit][1].append(f_item)
                        for synoym in check_synonyms(f_item, synonym_set, stopword_set):
                            vit_dict[cur_vit][1].append(f"{new_tag}:{synoym}")
                cur_line = file.readline()
            if(cur_vit != ''):
                vit_dict[cur_vit][1] = list(set(vit_dict[cur_vit][1]))
                print(cur_vit + f":\n{vit_dict[cur_vit]}\n")
        cur_line = file.readline()
    file.close()

vitamin-a:
[[], ['fr:vitmine-', 'he:ויטמין-a', 'ro:vitamina-a', 'ja:ビタミンa', 'pl:witamina-a', 'lt:vitaminas-a', 'pt:vitamina-a', 'en:vitamin-a', 'el:βιταμίνη-a', 'ja:v.a', 'pt:vitmin-', 'et:a-vitamiin', 'ja:ビタミン-ａ', 'fr:vitamine-pro-a', 'ja:ビタミンａ', 'lv:a-vitamīns', 'fi:a-vitamiini', 'it:vitamina-a', 'zh:维生素a', 'ja:v-a', 'ja:ｖ．ａ', 'de:vitamin-a', 'fr:vitmine-pro-', 'bg:витамин-а', 'fr:vitamine-a', 'sk:vitamín-a', 'mt:vitamina-a', 'ja:ｖーａ', 'hu:a-vitamin', 'he:רטינול', 'nl:vitamine-a', 'ja:ビタミン-a', 'es:vitamina-a']]

retinol:
[['vitamin-a'], ['et:retinool', 'lv:retinols', 'en:retinol', 'el:ρετινόλη', 'hu:retinol', 'bg:ретинол', 'lt:retinolis', 'de:retinol', 'es:retinol', 'fr:rétinol', 'fi:retinoli', 'nl:retinol', 'it:retinolo']]

retinyl-acetate:
[['vitamin-a'], ['fa:استات-رتینیل', 'fi:retinyyliasetaatti', 'en:retinol-acetate', 'sk:retinylacetát', 'de:retinylacetat', 'fr:acétate-rétinol', 'el:οξική-ρετινόλη', 'en:retinyl-acetate', 'mt:aċetat-tar-retinil', 'sr:retinil-acetat', 'es:acetato-

d-alpha-tocopherol:
[['vitamin-e'], ['hu:d-alfa-tokoferol', 'de:d-alpha-tocopherol', 'bg:d-алфа-токоферол', 'mt:d-alfa-tokoferol', 'pl:d-alfa-tokoferol', 'ro:tocoferol-d-alfa', 'es:d-alfa-tocoferol', 'fr:-alpha-tocophérol', 'sv:d-alfa-tokoferol', 'pt:d-alfa-tocoferol', 'lt:d-alfa-tokoferolis', 'fi:d-alfa-tokoferoli', 'cs:d-α-tokoferol', 'sl:d-alfa-tokoferol', 'fr:d-alpha-tocophérol', 'it:d-alfa-tocoferolo', 'lv:d-alfa-tokoferols', 'el:d-α-τοκοφερόλη', 'et:d-alfa-tokoferool', 'sk:d-alfa-tokoferol', 'en:d-alpha-tocopherol', 'nl:d-alfa-tocoferol']]

d-alpha-tocopheryl-acetate:
[['vitamin-e'], ['pt:acetato-de-d-alfa-tocoferilo', 'fr:acétate-de-d-alpha-tocophérol', 'fi:d-alfa-tokoferyyliasetaatti', 'en:d-alpha-tocopheryl-acetate', 'en:alpha-tocopherol-acetate', 'bg:d-алфатокоферил-ацетат', 'pl:octan-d-alfa-tokoferylu', 'hu:d-alfa-tokoferil-acetát', 'fr:acétate-d-alpha-tocophérol', 'it:acetato-di-d-alfa-tocoferile', 'es:acetato-de-d-alfa-tocoferilo', 'en:alpha-tocopheryl-acetate', 'lv:d-alfa

l-ascorbic-acid:
[['vitamin-c'], ['lt:askorbo-rūgštis', 'cs:l-askorbová-kyselina', 'gl:ácido-ascórbico', 'sk:kyselina-askorbová', 'fr:acide-ascorbique', 'bg:аскорбинова-киселина', 'pl:kwas-l-askorbinowy', 'en:ascorbic-acid', 'lv:askorbīnskābe', 'et:l-askorbiinhape', 'pl:kwas-askorbinowy', 'lv:l-askorbīnskābe', 'fi:askorbiinihappo', 'es:ácido-l-ascórbico', 'mt:aċidu-askorbiku', 'sl:askorbinska-kislina', 'hu:l-aszkorbinsav', 'bs:askorbinska-kiselina', 'el:ασκορβικό-οξύ', 'ca:àcid-ascòrbic', 'ro:acid-l-ascorbic', 'it:acido-l-ascorbico', 'sv:l-askorbinsyra', 'nl:l-ascorbinezuur', 'fi:l-askorbiinihappo', 'hr:askorbinska-kiselina', 'de:l-ascorbinsäure', 'es:ácido-ascórbico', 'de:ascorbinsäure', 'ja:アスコルビン酸', 'lt:l–askorbo-rūgštis', 'cs:askorbová-kyselina', 'sk:kyselina-l-askorbová', 'fr:acide-l-ascorbique', 'it:acido-ascorbico', 'el:l-ασκορβικό-οξύ', 'tr:askorbik-asit', 'en:l-ascorbic-acid', 'et:askorbiinhape', 'hr:l-askorbinska-kiselina', 'nl:ascorbinezuur', 'bg:l-аскорбинова-киселина', 'ru

nicotinic-acid:
[['niacin'], ['bg:никотинова-киселина', 'fr:acide-nicotinique', 'en:nicotinic-acid', 'de:nicotinsäure', 'mt:aċidu-nikotoniku', 'cs:kyselina-nikotinová', 'sl:nikotinska-kislina', 'lv:nikotīnskābe', 'fi:nikotiinihappo', 'es:ácido-nicotínico', 'et:nikotiinhape', 'el:νικοτινικό-οξύ', 'lt:nikotino-rūgštis', 'it:acido-nicotinico', 'sv:nikotinsyra', 'sk:kyselina-nikotínová', 'ro:acid-nicotinic', 'pl:kwas-nikotynowy', 'nl:nicotinezuur', 'pt:ácido-nicotínico', 'hu:nikotinsav']]

nicotinamide:
[['niacin'], ['nl:nicotinamide', 'de:nicotinamid', 'hu:nikotinamid', 'lv:nikotīnamīds', 'pt:nicotinamida', 'el:νικοτιναμίδιο', 'en:nicotinamide', 'bg:никотинамид', 'et:nikotiinamiid', 'es:nicotinamida', 'sk:nikotínamid', 'mt:nikotinamide', 'fi:nikotiiniamidi', 'pl:amid-kwasu-nikotynowego', 'sv:nikotinamid', 'pl:nikotynamid', 'lt:nikotinamidas', 'cs:nikotinamid', 'ro:nicotinamidă', 'sl:nikotinamid']]

vitamin-b6:
[[], ['ja:ｖーｂ６', 'pt:vitamina-b6', 'sk:vitamín-b6', 'ro:vitamina-b6', 'ja:ビタミン-

hydroxocobalamin:
[['vitamin-b12'], ['fi:hydroksokobalamiini', 'pt:hidroxocobalamine', 'cs:hydroxokobalamin', 'mt:idrossokobalamina', 'lt:hidroksokobalaminas', 'ro:hidroxocobalamină', 'nl:hydroxocobalamine', 'et:hüdroksokobalamiin', 'sl:hidroksokobalamin', 'hu:hidroxokobalamin', 'sk:hydroxokobalamín', 'lv:hidroksokobalamīns', 'es:hidroxocobalamina', 'bg:хидроксокобаламин', 'it:idrossocobalamina', 'en:hydroxocobalamin', 'el:υδροξοκοβαλαμίνη', 'pl:hydroksokobalamina', 'fr:hydroxocobalamine', 'sv:hydroxykobalamin']]

biotin:
[[], ['lt:biotinas', 'sk:biotín', 'ro:biotină', 'en:biotin', 'fr:vitamine-h', 'et:biotiin', 'nl:biotine', 'fr:biotine', 'pt:biotina', 'hu:h-vitamin', 'lv:biotīns', 'hr:biotin', 'es:biotina', 'it:biotina', 'es:vitamina-b7', 'bg:биотин', 'hu:b7-vitamin', 'pl:biotyna', 'hu:biotin', 'fi:biotiini', 'mt:bijotina', 'el:βιοτίνη', 'fr:vitamine-b7']]

d-biotin:
[['biotin'], ['nl:d-biotine', 'hu:d-biotin', 'en:d-biotin', 'hr:d-biotin']]

vitamin-b8:
[['biotin'], ['ja:v-b₈', 'pl:

Packaging

In [9]:
# Read the taxonomy line by line and add each element to a dictionary

packaging_tx_map = {}
master = ''
master_tag = ''
start = True
count_masters = 0


with open(packaging_materials_tx, 'r', encoding='utf-8') as file:
    
    for line in file:
        
        # Iterate until ingredients (deactivated)
        if start and 'en:Plastic' not in line:
            continue
        else:
            start = False
            
        # Check if there is a new section
        if line == '\n':
            master = ''
            #print('reset')
            
        # Skip the line if is a comment or if is not a valid line
        if '#' in line or line.count(':') != 1 or '<' in line:
            continue
        
        line = line.lower() #IMPORTANT
        language_tag, ingredients = split_line(line)
        
        # Add the line to the dictionary
        if language_tag == 'en' or master == '':
            master = ingredients[0]
            master_tag = language_tag
            count_masters += 1
        
        for ingredient in ingredients:
            ingredient = ingredient
            packaging_tx_map[language_tag+':'+ingredient] = master_tag+':'+master
        
        
    print('# of elements in the dictionary: ' + str(len(packaging_tx_map)))
    print('# of master elements in the dictionary: ' + str(count_masters) + '\n')
        
        
        
master = ''
master_tag = ''
start = True        
        
with open(packaging_shapes_tx, 'r', encoding='utf-8') as file:
    
    for line in file:
        
        # Iterate until ingredients (deactivated)
        if start and 'en:packaging' not in line:
            continue
        else:
            start = False
            
        # Check if there is a new section
        if line == '\n':
            master = ''
            #print('reset')
            
        # Skip the line if is a comment or if is not a valid line
        if '#' in line or line.count(':') != 1 or '<' in line:
            continue
        
        line = line.lower() # IMPORTANT
        language_tag, ingredients = split_line(line)
        
        # Add the line to the dictionary
        if language_tag == 'en' or master == '':
            master = ingredients[0]
            master_tag = language_tag
            count_masters += 1
        
        for ingredient in ingredients:
            ingredient = ingredient
            packaging_tx_map[language_tag+':'+ingredient] = master_tag+':'+master
        
        
    print('# of elements in the dictionary: ' + str(len(packaging_tx_map)))
    print('# of master elements in the dictionary: ' + str(count_masters) + '\n')
    print(packaging_tx_map)


# of elements in the dictionary: 2798
# of master elements in the dictionary: 292

# of elements in the dictionary: 4367
# of master elements in the dictionary: 414

{'en:plastic': 'en:plastic', 'ar:بلاستيك': 'en:plastic', 'be:пластма́са': 'en:plastic', 'bg:пластмаса': 'en:plastic', 'ca:plàstic': 'en:plastic', 'cs:umělá-hmota': 'en:plastic', 'da:plast': 'en:plastic', 'de:kunststoff': 'en:plastic', 'de:kunstoff': 'en:plastic', 'de:plastik': 'en:plastic', 'el:πλαστικό': 'en:plastic', 'es:plástico': 'en:plastic', 'et:plast': 'en:plastic', 'fi:muovi': 'en:plastic', 'fr:plastique': 'en:plastic', 'he:פלסטיק': 'en:plastic', 'hr:plastika': 'en:plastic', 'hu:műanyag': 'en:plastic', 'is:plast': 'en:plastic', 'it:plastica': 'en:plastic', 'ja:プラスチック': 'en:plastic', 'ko:플라스틱': 'en:plastic', 'lt:plastikas': 'en:plastic', 'lv:plastmasa': 'en:plastic', 'mk:пластика': 'en:plastic', 'nl:plastic': 'en:plastic', 'nl:plastiek': 'en:plastic', 'no:plast': 'en:plastic', 'pl:plastik': 'en:plastic', 'pl:plastik

In [10]:
pack_dict = {}

with open(packaging_materials_tx, 'r', encoding='utf-8') as file:
    
    cur_line = file.readline()
    while cur_line != '':
        cur_pack = ''
        super_items = []
        if re.match('^<?[a-z]{2}:', cur_line):
            while re.match('^<[a-z]{2}:', cur_line):
                new_item = re.match('^<[a-z]{2}:[^#]*', cur_line).group()
                new_item = re.split(':', new_item)[1]
                super_items.append(re.sub('"', "'", re.sub('--+', '-', new_item.strip().lower().replace(' ', '-'))))
                cur_line = file.readline()
            while cur_line != '\n' and cur_line != '':
                if re.match('^[a-z]{2}:', cur_line):
                    new_item = re.match('^[a-z]{2}:[^#]*', cur_line).group()
                    new_item = re.split(':', new_item)
                    new_tag = new_item[0]
                    new_items = re.split(',', new_item[1])
                    for item in new_items:
                        item = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                    if cur_pack == '':
                        cur_pack = re.sub('"', "'", re.sub('--+', '-', new_items[0].strip().lower().replace(' ', '-')))
                        pack_dict[cur_pack] = [super_items,[]]
                    for item in new_items:
                        f_name = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                        f_item = f"{new_tag}:{f_name}"
                        pack_dict[cur_pack][1].append(f_item)
                        for synoym in check_synonyms(f_item, synonym_set, stopword_set):
                            pack_dict[cur_pack][1].append(f"{new_tag}:{synoym}")
                cur_line = file.readline()
            if(cur_pack != ''):
                pack_dict[cur_pack][1] = list(set(pack_dict[cur_pack][1]))
                print(cur_pack + f":\n{pack_dict[cur_pack]}\n")
        cur_line = file.readline()
    file.close()
    
    
with open(packaging_shapes_tx, 'r', encoding='utf-8') as file:
    
    cur_line = file.readline()
    while cur_line != '':
        cur_pack = ''
        super_items = []
        if re.match('^<?[a-z]{2}:', cur_line):
            while re.match('^<[a-z]{2}:', cur_line):
                new_item = re.match('^<[a-z]{2}:[^#]*', cur_line).group()
                new_item = re.split(':', new_item)[1]
                super_items.append(re.sub('"', "'", re.sub('--+', '-', new_item.strip().lower().replace(' ', '-'))))
                cur_line = file.readline()
            while cur_line != '\n' and cur_line != '':
                if re.match('^[a-z]{2}:', cur_line):
                    new_item = re.match('^[a-z]{2}:[^#]*', cur_line).group()
                    new_item = re.split(':', new_item)
                    new_tag = new_item[0]
                    new_items = re.split(',', new_item[1])
                    for item in new_items:
                        item = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                    if cur_pack == '':
                        cur_pack = re.sub('"', "'", re.sub('--+', '-', new_items[0].strip().lower().replace(' ', '-')))
                        pack_dict[cur_pack] = [super_items,[]]
                    for item in new_items:
                        f_name = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                        f_item = f"{new_tag}:{f_name}"
                        pack_dict[cur_pack][1].append(f_item)
                        for synoym in check_synonyms(f_item, synonym_set, stopword_set):
                            pack_dict[cur_pack][1].append(f"{new_tag}:{synoym}")
                cur_line = file.readline()
            if(cur_pack != ''):
                pack_dict[cur_pack][1] = list(set(pack_dict[cur_pack][1]))
                print(cur_pack + f":\n{pack_dict[cur_pack]}\n")
        cur_line = file.readline()
    file.close()

unknown:
[[], ['bg:неизвестно', 'nl:onbekend', 'fr:inconnues', 'fr:inconnue', 'fr:inconnus', 'fr:inconnu', 'en:unknown', 'de:unbekannt', 'hu:ismeretlen']]

plastic:
[[], ['de:kunstoff', 'mk:пластика', 'it:plastica', 'uk:пластма́са', 'sv:plast', 'be:пластма́са', 'lv:plastmasa', 'sl:plastika', 'zh:塑料', 'da:plast', 'ko:플라스틱', 'hu:műanyag', 'de:plastik', 'es:plástico', 'ca:plàstic', 'ar:بلاستيك', 'fr:plastique', 'ru:пластик', 'pl:plastik', 'en:plastic', 'cs:umělá-hmota', 'he:פלסטיק', 'nl:plastic', 'pt:plástico', 'lt:plastikas', 'fi:muovi', 'is:plast', 'pl:plastikowe', 'tr:plastik', 'hr:plastika', 'bg:пластмаса', 'de:kunststoff', 'ja:プラスチック', 'nl:plastiek', 'el:πλαστικό', 'et:plast', 'sk:plast', 'no:plast']]

composite-material:
[[], ['sv:kompositmaterial', 'ja:複合材料', 'de:verbundwerkstoff', 'zh:复合材料', 'fr:multi-couches', 'en:composite', 'sk:kompozitný-materiál', 'de:mehrschicht', 'es:material-compuesto', 'en:composite-materials', 'ca:material-compost', 'eu:material-konposatu', 'pt:compósito

rpet-transparent:
[['rpet'], ['fr:rpet-clair', 'nl:rpet-transparant', 'pt:rpet-transparente', 'en:rpet-transparent', 'en:transparent-rpet', 'da:rpet-gennemsigtig', 'en:clear-rpet', 'de:rpet-transparentes', 'fr:rpet-transparente', 'hu:rpet-átlátszó', 'nl:transparant-rpet', 'fr:rpet-transparent']]

pet-colored:
[['pet'], ['fr:pet-colorée', 'de:pet-gefärbtes', 'da:pet-farvet', 'en:pet-colored', 'hu:színes-pet', 'hu:pet-színezet', 'en:colored-pet', 'fr:pet-coloré', 'de:farbiges-pet', 'nl:pet-gekleurd', 'nl:gekleurd-pet', 'pt:pet-colorido']]

pet-opaque:
[['pet'], ['fr:pet-opaque', 'it:pet-opaco', 'de:intransparentes-pet', 'en:pet-opaque', 'en:opaque-pet', 'nl:ondoorzichtig-pet', 'de:pet-undurchsichtiges', 'es:pet-opaco', 'nl:pet-ondoorzichtig', 'pt:pet-opaco']]

pe-7-polyethylene:
[['plastic'], ['xx:pe7', 'sk:polyetylén', 'lv:pe-polietilēns', 'pt:pe-polietileno', 'xx:7-pe', 'is:pe-7-fjöletýlen', 'hu:pe-7-polietilén', 'nn:pe-polyetylen', 'fi:pe-7-polyeteeni', 'da:pe-7-polyethylen', 'ro:poli

bio-ldpe-biobased-ldpe:
[['ldpe', 'bio-pe'], ['fr:bio-peld-peld-biosourcé', 'fr:peld-biosourcé', 'fr:bio-peld-peld-bio-sourcé', 'xx:bio-ldpe', 'en:bio-ldpe-bio-sourced-ldpe', 'hu:biobázisú-ldpe', 'en:bio-ldpe-bio-based-ldpe', 'fr:ldpe-biosourcé', 'en:biobased-ldpe', 'en:bio-ldpe-biobased-ldpe', 'de:biobasiertes-pe-ld', 'fr:ldpe-bio-sourcé', 'nl:biologische-ldpe', 'pt:bio-peld-bioplástico-peld', 'pt:bioplástico-peld', 'nl:bio-ldpe-biologische-ldpe', 'hu:bio-ldpe-biobázisú-ldpe', 'en:bio-ldpe-biosourced-ldpe', 'xx:bldpe', 'en:bio-based-ldpe', 'fr:peld-bio-sourcé', 'de:biobasiertes-ldpe', 'en:bio-sourced-ldpe', 'de:bio-ldpe-biobasiertes-ldpe', 'en:biosourced-ldpe']]

pp-5-polypropylene:
[['plastic'], ['cs:polypropylen', 'hr:polipropilen', 'xx:pp-05', 'xx:05-pp', 'nb:pp-5-polypropen', 'en:pp-5-polypropylene', 'sr:pp-5-полипропилен', 'xx:♷', 'it:polipropilene', 'fi:polypropeeni', 'it:pp-5-polipropilene', 'nl:pp-5-polypropeen', 'sk:polypropylén', 'sk:pp-5-polypropylén', 'ro:polipropilenă', '

pmma-poly(methyl-methacrylate):
[['plastic', 'other-plastics'], ['de:pmma-polymethylmethacrylat', 'pt:acrílico', 'en:pmma-poly(methyl-methacrylate)', 'nb:polymetylmetakrylat', 'de:acrylglas', 'nn:pmma-polymetylmetakrylat', 'tr:pleksi', 'da:akryl', 'fi:pmma-akryyli', 'fr:poly(méthacrylate-de-méthyle)', 'fi:akryyli', 'hu:poli-metil-metakrilát', 'xx:07pmma', 'en:poly(methyl-methacrylate)', 'uk:органічне-скло', 'de:polymethylmethacrylat', 'tr:pmma-pleksi', 'sr:pleksiglas', 'cs:polymethylmethakrylát', 'da:pmma-akryl', 'ca:polimetilmetacrilat', 'it:polimetilmetacrilato', 'xx:pmma7', 'pl:poli(metakrylan-metylu)', 'sk:polymetylmetakrylát', 'es:pmma-polimetilmetacrilato', 'xx:pmma-07', 'xx:pmma07', 'sr:плексиглас', 'xx:07-pmma', 'ru:органическое-стекло', 'pt:pmma-acrílico', 'bg:полиметилметакрилат', 'nl:polymethylmethacrylaat', 'es:polimetilmetacrilato', 'el:pmma-πολυμεθακρυλικό-μεθύλιο', 'ga:peirspéacs', 'sl:polimetilmetaakrilat', 'bg:pmma-полиметилметакрилат', 'sl:pmma-polimetilmetaakrilat', 

zinc–carbon-battery:
[[], ['nl:zink-koolstofcel', 'de:zink–kohle-batterie', 'hu:co2-cink-akkumulátor', 'hu:szén-cink-elem', 'hu:co2-cink-elem', 'pt:bateria-zinco-carbono', 'pt:bateria-de-zinco-carbono', 'pt:pilha-zinco-carbono', 'pt:pilha-de-zinco-carbono', 'hu:szén-cink-akkumulátor', 'pt:bateria-de-zinco-co2', 'pt:pilha-de-zinco-co2', 'xx:14-cz', 'hr:cink-ugljik-baterija', 'hu:cink-co2-akkumulátor', 'xx:cz-14', 'en:zinc–carbon-battery', 'hu:cink-szén-akkumulátor']]

paper-or-cardboard:
[[], ['fr:papier-carton', 'en:paper-cardboard', 'fr:papier-ou-carton', 'en:paper-or-cardboard']]

cardboard:
[['paper-or-cardboard'], ['nl:strokarton', 'nl:vouwkarton', 'ro:carton', 'hu:kartondoboz', 'nl:turfkarton', 'en:fibreboard', 'de:karton', 'ru:картон', 'nl:vormkarton', 'sv:kartong', 'fr:carton', 'hr:karton', 'lt:kartonas', 'hu:hullámpapír-kartondoboz', 'pl:karton', 'pt:cartonada', 'en:cardboard', 'pt:cartão-canelado', 'pt:cartonado', 'fr:carton-standard', 'fi:pahvi', 'da:karton', 'fr:cartonné', '

...

paper-and-fibreboard/aluminium:
[['multilayer-composite'], ['en:paper-and-fibreboard-+-aluminium', 'de:papier-und-pappe/aluminium', 'xx:82-c/*', 'de:papier-pappe/aluminium', 'de:papier-pappe-+-aluminium', 'en:paper-and-fibreboard/aluminium', 'de:papier-und-pappe-+-aluminium', 'xx:82-c/x', 'xx:82-cx', 'xx:82-c*', 'hr:papir-i-karton/aluminij', 'hr:papr-karton/alumnj']]

82-c/pap:
[['82-c/x'], ['xx:82-c/pap']]

82-c/alu:
[['82-c/x'], ['xx:82-c/alu']]

paper-and-fibreboard/tinplate:
[['multilayer-composite'], ['xx:83-c/x', 'de:papier-pappe-+-weissblech', 'hr:papir-i-karton/bijeli-lim', 'en:paper-and-fibreboard-+-tinplate', 'de:papier-pappe/weissblech', 'hr:papr-karton/bjel-lm', 'xx:83-c/*', 'de:papier-pappe/weißblech', 'de:papier-und-pappe-+-weissblech', 'de:papier-und-pappe-+-weißblech', 'de:papier-und-pappe/weissblech', 'xx:83-cx', 'xx:83-c*', 'de:papier-und-pappe/weißblech', 'en:paper-and-fibreboard/tinplate', 'de:papier-pappe-+-weißblech']]

83-c/pap:
[['83-c/x'], ['xx:83-c/pap']]

83-

tetra-brik:
[['tetra-pak'], ['xx:tetra-brik', 'en:tetra-brik']]

tetra-brik-aseptic:
[['tetra-pak'], ['xx:tetra-brik-aseptic', 'en:tetra-brik-aseptic']]

tetra-rex:
[['tetra-pak'], ['xx:tetra-rex', 'en:tetra-rex']]

tetra-top:
[['tetra-pak'], ['en:tetra-top', 'xx:tetra-top']]

tetra-stelo-aseptic:
[['tetra-pak'], ['en:tetra-stelo', 'xx:tetra-stelo-aseptic', 'en:tetra-stelo-aseptic', 'xx:tetra-stelo']]

tetra-fino-aseptic:
[['tetra-pak'], ['en:tetra-fino', 'xx:tetra-fino', 'en:tetra-fino-aseptic', 'xx:tetra-fino-aseptic']]

tetra-classic-aseptic:
[['tetra-pak'], ['en:tetra-classic', 'en:tetra-classic-aseptic', 'xx:tetra-classic-aseptic', 'xx:tetra-classic']]

tetra-gemina-aseptic:
[['tetra-pak'], ['en:tetra-gemina-aseptic', 'en:tetra-gemina', 'xx:tetra-gemina-aseptic', 'xx:tetra-gemina']]

tetra-wedge-aseptic:
[['tetra-pak'], ['en:tetra-wedge-aseptic', 'xx:tetra-wedge', 'xx:tetra-wedge-aseptic', 'en:tetra-wedge']]

tetra-prisma-aseptic:
[['tetra-pak'], ['en:tetra-prisma-aseptic', 'xx:te

small-brick:
[[], ['en:small-bricks', 'nl:briquettes', 'nl:briquette', 'en:small-brick', 'fr:briquette', 'fr:briquettes']]

can:
[[], ['pl:puszka', 'bg:консерва-кен', 'es:lata', 'fr:boîtes-de-conserve-ou-canettes', 'en:can', 'pt:lata', 'it:lattina', 'da:dåser', 'fr:boîte-de-conserve-ou-canette', 'fr:boîtes-de-conserve-canettes', 'nl:bus', 'hu:konzervdoboz', 'en:cans', 'fr:boîtes-conserve-ou-canettes', 'de:dosen', 'bg:консерва-или-кен', 'nl:blik', 'de:dose', 'it:latta', 'hu:konzerv', 'pt:latas', 'fr:boîte-de-conserve-canette', 'fr:boîte-conserve-ou-canette', 'da:dåse', 'hr:limenka']]

drink-can:
[['can'], ['bg:кенче', 'en:drink-can', 'bg:кен', 'pt:lata-refrigerante', 'pt:lata-bebida', 'pt:lata-de-alumínio', 'pt:lata-de-bebida', 'pt:lata-alumínio', 'pt:latas-refrigerantes', 'pt:lata-de-refrigerante', 'fr:canette', 'pt:latas-alumínio', 'pt:latas-de-refrigerante', 'pt:latas-bebidas', 'hu:konzervital', 'fr:boites-boissons', 'fr:cannette', 'pt:lata-refrigerantes', 'pt:latas-de-alumínio', 'pl

coffee-capsule:
[[], ['fr:capsules-de-café', 'pt:cápsulas-cafés', 'pt:cápsulas-de-café', 'nl:koffiecapsule', 'hu:kávé-kapszulák', 'nl:nespresso-capsule', 'fr:capsule-de-café', 'pt:cápsula-cafés', 'hu:kávé-kapszula', 'pt:cápsula-de-café', 'fr:capsules-café', 'en:coffee-capsules', 'pl:kapsułka-do-kawy', 'pt:cápsula-de-cafés', 'hu:kávékapszula', 'fr:capsule-café', 'pt:cápsula-café', 'nl:nespressocapsule', 'pt:cápsulas-café', 'hu:kávékapszulák', 'en:coffee-capsule', 'nl:koffiecapsules', 'pt:cápsulas-de-cafés']]

nespresso-compatible-capsules:
[['coffee-capsule'], ['fr:dosettes-nespresso', 'fr:dosettes-compatible-nespresso', 'es:cápsulas-compatibles-nespresso', 'en:nespresso-compatible-capsules', 'nl:nespresso', 'it:capsule-compatibili-nespresso', 'fr:capsules-nespresso', 'lt:nespresso-kapsulės', 'de:nespresso-kompatible-kapseln', 'nl:nespresso-compatibele-capsules', 'es:cápsulas-compatibles-con-nespresso', 'fi:nespresso-yhteensopivat-kapselit']]

tassimo-compatible-capsules:
[['coffee-caps

cosmetic-stick:
[[], ['fr:stick-cosmétique', 'en:cosmetic-stick']]

label:
[[], ['pl:etykieta', 'bg:етикет', 'pt:etiquetas', 'hu:címke', 'pl:etykiety', 'pt:rótulo', 'en:labels', 'bg:етикети', 'hu:címkék', 'nl:labels', 'nl:label', 'pt:rótulos', 'fr:étiquettes', 'fr:étiquette', 'de:etikett', 'en:label', 'de:etiketten', 'pt:etiqueta']]

applicator:
[[], ['fr:applicateur', 'en:applicator', 'nl:applicator']]

bag-in-box:
[[], ['nl:zak-in-doos', 'fr:cubitainer', 'fr:bag-in-box', 'fr:bib', 'en:bag-in-box', 'fr:caisse-outre']]

strip:
[[], ['en:tab', 'en:strip', 'fr:bandes', 'fr:bande', 'fr:bandelette', 'en:band', 'fr:languette', 'fr:languettes', 'fr:bandelettes']]

ampoule:
[[], ['en:ampoule', 'fr:ampoule', 'en:ampule', 'en:ampul', 'hr:ampula', 'nl:ampulle', 'bg:крушка']]

blister:
[[], ['nl:blister', 'en:blister-pack', 'fr:blister', 'en:blister', 'bg:блистер']]

roll:
[[], ['en:mandrel', 'fr:rouleau', 'fr:mandrin-/-rouleau', 'en:roll', 'fr:mandrin', 'fr:bobine']]

jug-or-canister:
[[], ['fr:

Labels

In [11]:
lab_dict = {}

with open(labels_tx, 'r', encoding='utf-8') as file:
    
    cur_line = file.readline()
    while cur_line != '':
        cur_lab = ''
        super_items = []
        if re.match('^<?[a-z]{2}:', cur_line):
            while re.match('^<[a-z]{2}:', cur_line):
                new_item = re.match('^<[a-z]{2}:[^#]*', cur_line).group()
                new_item = re.split(':', new_item)[1]
                super_items.append(re.sub('"', "'", re.sub('--+', '-', new_item.strip().lower().replace(' ', '-'))))
                cur_line = file.readline()
            while cur_line != '\n' and cur_line != '':
                if re.match('^[a-z]{2}:', cur_line):
                    new_item = re.match('^[a-z]{2}:[^#]*', cur_line).group()
                    new_item = re.split(':', new_item)
                    new_tag = new_item[0]
                    new_items = re.split(',', new_item[1])
                    for item in new_items:
                        item = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                    if cur_lab == '':
                        cur_lab = re.sub('"', "'", re.sub('--+', '-', new_items[0].strip().lower().replace(' ', '-')))
                        lab_dict[cur_lab] = [super_items,[]]
                    for item in new_items:
                        f_name = re.sub('"', "'", re.sub('--+', '-', item.strip().lower().replace(' ', '-')))
                        f_item = f"{new_tag}:{f_name}"
                        lab_dict[cur_lab][1].append(f_item)
                        for synoym in check_synonyms(f_item, synonym_set, stopword_set):
                            lab_dict[cur_lab][1].append(f"{new_tag}:{synoym}")
                cur_line = file.readline()
            if(cur_lab != ''):
                lab_dict[cur_lab][1] = list(set(lab_dict[cur_lab][1]))
                print(cur_lab + f":\n{lab_dict[cur_lab]}\n")
        cur_line = file.readline()
    file.close()

1%-for-the-planet:
[[], ['es:uno-ciento-para-el-planeta', 'fi:prosentti-planeetalle', 'en:one-percent-for-the-planet', 'pt:1-porcento-o-planeta', 'pt:1-cento-para-o-planeta', 'it:1%-per-il-pianeta', 'en:1-percent-for-planet', 'pt:um-porcento-para-o-planeta', 'es:uno-por-ciento-el-planeta', 'pt:um-porcento-o-planeta', 'pt:1%-para-o-planeta', 'es:1%-el-planeta', 'es:uno-por-ciento-para-el-planeta', 'pt:1-por-cento-para-o-planeta', 'bg:1%-за-планетата', 'es:1%-para-el-planeta', 'fi:1%-planeetalle', 'pt:um-cento-para-o-planeta', 'pt:1-por-cento-o-planeta', 'pt:um-por-cento-para-o-planeta', 'fr:1%-pour-pnète', 'pt:1%-o-planeta', 'es:1%-para-planeta', 'en:one-percent-for-planet', 'fr:1%-pour-la-planète', 'de:1%-für-den-planeten', 'en:1%-for-the-planet', 'en:no1-percent-for-the-planet', 'pt:um-por-cento-o-planeta', 'en:1-percent-for-the-planet', 'pt:1-porcento-para-o-planeta', 'nl:1%-voor-de-planeet', 'en:1%-for-planet', 'pt:1%-para-planeta', 'pt:um-prcent-para-planeta', 'pt:um-pr-cent-para-p

made-with-free-range-eggs:
[['free-range-eggs'], ['fr:fait-avec-œufs-de-poules-en-liberté', 'de:enhält-freilandeier', 'ca:fet-amb-ous-gallines-crias-lliures', 'pt:fabricado-com-ovos-de-galinhas-em-liberdade', 'pt:feito-ovos-de-galinhas-criadas-ao-ar-livre', 'pt:feito-com-ovos-de-galinhas-criadas-ao-ar-livre', 'fr:fait-avec-des-œufs-de-poules-élevé-en-liberté', 'fr:fait-avec-s-œufs-poules-en-liberté', 'pt:fabrico-com-ovos-de-galinhas-livres-de-gaiolas', 'pt:elaborado-com-ovos-de-galinhas-criadas-ao-ar-livre', 'fr:fait-avec-des-œufs-de-poules-élevées-plein-air', 'pt:elaborado-com-ovos-de-galinhas-criadas-em-liberdade', 'fr:cuisiné-des-œufs-de-plein-air', 'fr:fait-avec-s-œufs-poules-élevées-en-liberté', 'pt:fabricado-com-ovos-de-galinhas-livres-de-gaiolas', 'pt:feito-com-ovos-galinhas-livres-gaiolas', 'pt:fabrico-com-ovos-de-galinhas-ao-ar-livre', 'pt:fabrico-com-ovos-de-galinhas-criadas-ao-ar-livre', 'de:aus-freilandeiern', 'fr:fait-des-œufs-de-poules-en-liberté', 'fr:fait-avec-des-œufs-

co2e-neutral:
[['carbon-compensated-product'], ['en:co2-equivalent-compensated', 'en:co2e-compensated', 'de:co2e-kompensiert', 'en:co2-equivalent-neutral', 'da:co2e-neutral', 'pt:compensado-em-co2e', 'pt:compensado-em-carbono', 'pt:compensado-co2e', 'pt:neutro-em-carbono', 'da:co2e-kompenseret', 'pt:compensado-carbono', 'en:carbon-equivalent-compensated', 'pt:neutro-co2', 'de:co2e-neutral', 'pt:neutro-em-co2', 'de:co2-äquivalent-kompensiert', 'pt:neutro-em-co2e', 'de:co2-äquivalent-neutral', 'pt:neutro-co2e', 'en:carbon-equivalent-neutral', 'pt:compensado-em-co2', 'en:co2e-neutral']]

carbon-footprint:
[[], ['bg:въглероден-отпечатък', 'pt:emissões-co2', 'es:emisiones-de-carbono', 'ru:co<sub>2</sub>-эмиссия', 'en:carbon-footprint', 'it:emissioni-di-co2', 'fi:hiilijalanjäljen-määrittelevä-', 'nl:klimaatafdruk', 'pl:ślad-węglowy-produktu', 'it:emissioni-di-carbonio', 'es:huella-carbono', 'pt:pegada-carbono', 'fi:hiilipäästöt', 'lt:anglies-dioksido-pėdsakas', 'hu:szénlábnyom', 'en:product-

eauscar-2003-de-la-meilleure-eau-minérale-étrangère-catégorie-eau-pétillante:
[['eauscar'], ['fr:eauscar-2003-de-meilleure-eau-minérale-étrangère-catégorie-eau-pétilnte', 'xx:eauscar-2003-de-la-meilleure-eau-minérale-étrangère-catégorie-eau-pétillante', 'fr:eauscar-2003-la-meilleure-eau-minérale-étrangère-catégorie-eau-pétillante', 'fr:eauscar-2003-de-la-meilleure-eau-minérale-étrangère-catégorie-eau-pétillante']]

international-ice-cream-consortium-award:
[[], ['xx:iicc', 'en:iicc', 'en:international-ice-cream-consortium-award', 'xx:international-ice-cream-consortium-award']]

international-ice-cream-consortium-award-best-ice-cream-2019:
[['international-ice-cream-consortium-award'], ['xx:international-ice-cream-consortium-award-best-ice-cream-2019', 'en:international-ice-cream-consortium-award-best-ice-cream-2019']]

international-ice-cream-consortium-award-most-innovative-ice-cream-2019:
[['international-ice-cream-consortium-award'], ['xx:international-ice-cream-consortium-award-mos

iso-3632:
[[], ['xx:iso-3632', 'en:iso-3632']]

iso-9000:
[[], ['xx:iso-9000', 'en:iso-9000']]

iso-9000-2005:
[['iso-9000'], ['xx:iso-9000-2005', 'en:iso-9000-2005']]

iso-9001:
[[], ['fi:iso-9001', 'it:sistema-di-qualita-certificato-iso-9001', 'pt:iso-9001', 'pl:iso-9001', 'fr:iso-9001', 'fr:certifie-iso-9001', 'es:certificación-calidad-iso-9001', 'fr:la-certification-qualite-iso-9001', 'pt:sistema-de-gestão-da-qualidade-iso-9001', 'it:iso-9001', 'bg:iso-9001', 'hu:iso-9001-tanúsítvány', 'xx:iso-9001', 'en:iso-9001', 'es:iso-9001', 'fr:-certification-qualite-iso-9001', 'es:certificación-de-calidad-iso-9001', 'hu:iso-9001', 'pt:sistema-de-gestão-qualide-iso-9001', 'ru:iso-9001', 'it:uni-en-iso-9001', 'ru:исо-9001', 'pt:sistema-gestão-da-qualida-iso-9001', 'fi:iso-9001-laatujärjestelmäsertifikaatti']]

iso-9001-2000:
[['iso-9001'], ['ru:исо-9001-2000', 'ru:гост-р-исо-9001', 'en:iso-9001-2000', 'xx:iso-9001-2000']]

iso-9001-2008:
[['iso-9001'], ['en:iso-9001-2008-certified-qms', 'en:is

...

union-française-pour-la-santé-bucco-dentaire:
[['tooth-health-related-labels'], ['fr:union-française-pour-santé-bucco-dentaire', 'fr:ufsbd', 'fr:union-française-pour-la-santé-bucco-dentaire']]

european-fruit-juice-control-system:
[[], ['en:european-quality-control-system-for-juice-and-nectars-fruits-and-vegetables', 'en:european-fruit-juice-control-system', 'en:european-quality-control-system-for-juice', 'en:european-quality-control-system-for-juice-and-nectars-from-fruits-and-vegetables', 'en:eqcs']]

napsi-certified:
[[], ['fr:certifié-napsi', 'en:napsi', 'nl:napsi-certificatie', 'en:napsi-', 'ca:certificat-napsi', 'fr:certifiée-napsi', 'fr:-napsi', 'en:napsi-certified', 'fi:napsi-', 'fi:napsi-sertifioitu']]

new:
[[], ['fi:uusi', 'ru:новинка', 'it:nuovo', 'de:neu', 'es:nuevo', 'ca:nou', 'pl:nowy', 'pl:nowość', 'th:สินค้าใหม่', 'en:new', 'he:חדש', 'pt:novo', 'tr:yeni', 'fr:nouveau', 'pl:nowe', 'bg:ново', 'hu:új', 'nl:nieuw', 'pt:novidade']]

new-recipe:
[[], ['fr:nouvelle-recette', 

potatoes-from-france:
[[], ['pt:batata-de-frança', 'pt:batatas-francesas', 'es:patatas-originadas-en-francia', 'fi:perunoita-ranskasta', 'de:kartoffeln-frankreich', 'pt:batata-da-frança', 'nl:aardappelen-uit-frankrijk', 'de:kartoffeln-aus-frankreich', 'fr:pommes-terre-france', 'en:potatoes-france', 'pt:batatas-frança', 'pt:batata-francesa', 'pt:batatas-da-frança', 'ca:patates-frança', 'it:patate-dalla-francia', 'it:patate-francesi', 'fi:perunoiden-alkuperä-ranska', 'es:patatas-originadas-francia', 'pt:batatas-de-frança', 'en:potatoes-from-france', 'pt:batata-frança', 'ca:patates-de-frança', 'fr:pommes-de-terre-de-france']]

pommes-de-terre-origine-france:
[[], ['fr:pommes-terre-origine-france', 'fr:pommes-de-terre-origine-france']]

apples-from-france:
[[], ['pt:maça-francesa', 'en:apples-from-france', 'de:äpfel-frankreich', 'es:manzanas-francia', 'fi:omenien-alkuperä-ranska', 'pt:maçãs-frança', 'de:äpfel-aus-frankreich', 'es:manzanas-de-francia', 'pt:maçãs-de-frança', 'en:apples-franc

without-hormones:
[[], ['fr:élevé-0%-hormone', 'en:free-hormones', 'pt:criada-zero-hormonas', 'pt:criadas-0%-hormonas', 'de:aufzucht-ohne-hormone', 'pt:0%-hormonas', 'de:aufzucht-0%-hormone', 'de:0%-hormone', 'en:without-hormones', 'fi:kasvatettu-vapaa-hormoneja', 'fi:hormoniton', 'en:raised-free-hormones', 'fr:élevé-sans-hormone', 'pt:criadas-livre-de-hormonas', 'pt:criados-zero-hormonas', 'it:allevato-zero-ormoni', 'pt:criado-livre-de-hormonas', 'pt:criada-sem-hormonas', 'fi:kasvatettu-ilman-hormoneja', 'pt:criado-zero-hormonas', 'it:allevato-senza-ormoni', 'it:0%-ormoni', 'pt:criados-sem-hormonas', 'pt:criada-0%-hormonas', 'de:ohne-hormone', 'pt:sem-hormonas', 'pt:zero-hormonas', 'it:allevato-0%-ormoni', 'pt:criadas-sem-hormonas', 'fi:kasvatettu-0%-hormoneja', 'fr:0%-hormone', 'pt:criadas-zero-hormonas', 'it:zero-ormoni', 'pt:criado-sem-hormonas', 'fr:sans-hormone', 'en:raised-0%-hormones', 'it:senza-ormoni', 'pt:criados-0%-hormonas', 'pt:criados-livre-de-hormonas', 'en:0%-hormones'

cold-pressed:
[[], ['fr:pression-à-froid', 'en:cold-pressed', 'fr:haute-pression-à-froid', 'nl:koudgeperst']]

unfiltered:
[[], ['en:unfiltered', 'en:cloudy', 'de:trüb', 'de:naturtrüb']]

filtered:
[[], ['fr:non-filtrée', 'fr:clair', 'en:filtered', 'de:klar']]

haute-valeur-environnementale:
[[], ['xx:haute-valeur-environnementale', 'fr:haute-valeur-environnementale', 'fr:hve', 'xx:hve']]

produit-certifié:
[[], ['en:certified-product', 'fr:produit-certifié', 'fr:produit-', 'fr:cq-produit-', 'en:-product', 'fr:cq-produit-certifié', 'fr:cq-']]

certified-quality:
[[], ['en:certified-quality', 'fr:qualité-certifiée', 'en:-quality']]

qs-certification-mark:
[[], ['en:qs-certification-mark', 'de:qs-prüfzeichen', 'es:sello-de-certificación-qs', 'en:qs-certification-', 'es:sello-certificación-qs']]

institut-fresenius:
[[], ['de:institut-fresenius', 'de:institut-fresenius-lebensmittel-siegel', 'xx:institut-fresenius', 'en:institut-fresenius']]

choices:
[[], ['en:choices', 'de:bewusst-wählen

redondo-doc:
[[], ['pt:redondo-doc', 'pt:doc-redondo', 'pt:d.o.c.-redondo', 'pt:denominação-de-origem-controlada-redondo', 'pt:nominação-origem-controlada-redondo']]

doc-beira-interior:
[[], ['pt:nominação-origem-beira-interior', 'pt:denominação-de-origem-beira-interior', 'pt:doc-beira-interior', 'pt:d.o.c.-beira-interior', 'pt:beira-interior-doc']]

ig-terras-da-beira:
[[], ['pt:indicação-geográfica-terras-beira', 'pt:ig-terras-beira', 'pt:terras-da-beira-ig', 'pt:i.g.-terras-beira', 'pt:i.g.-terras-da-beira', 'pt:indicação-geográfica-terras-da-beira', 'pt:terras-beira-ig', 'pt:ig-terras-da-beira']]

doc-távora-varosa:
[[], ['pt:nominação-origem-távora-varosa', 'pt:d.o.c.-távora-varosa', 'pt:denominação-de-origem-távora-varosa', 'pt:távora-varosa-doc', 'pt:doc-távora-varosa']]

doc-borba:
[[], ['pt:borba-doc', 'pt:denominação-de-origem-controlada-borba', 'pt:d.o.c.-borba', 'pt:nominação-origem-controlada-borba', 'pt:doc-borba']]

doc-reguengos:
[[], ['pt:doc-reguengos', 'pt:nominação

## Data Visualization

Data Visualization...

In [ ]:
# Splits the entries in a DataFrame's target column based on a specified separator, 
# creating new rows for each element resulting from the split.

def splitDataFrameList(df, target_column, separator):
    def splitListToRows(row, row_accumulator, target_column, separator):
        split_row = row[target_column].split(separator)
        for s in split_row:
            new_row = row.to_dict()
            new_row[target_column] = s
            row_accumulator.append(new_row)
    new_rows = []
    df.apply(splitListToRows,axis=1,args = (new_rows,target_column,separator))
    new_df = pd.DataFrame(new_rows)
    return new_df

In [ ]:
# Print original dataset

countries = df["countries_en"].value_counts()

In [ ]:
# Plotting the horizontal bar chart

ax = countries[:15][::-1].plot.barh(figsize=(8, 4), color='skyblue')
plt.xlabel('Values')
plt.title('Top 15 Countries')


# Displaying the value of each bar on the plot

for i, v in enumerate(countries[:15][::-1]):
    ax.text(v + 500, i, str(v), color='black', va='center', fontsize=10)

plt.show()

In [ ]:
# Print new dataset

food_countries = splitDataFrameList(food_table, "countries_en", ",")
countries = food_countries["countries_en"].value_counts()

In [ ]:
# Plotting the horizontal bar chart

ax = countries[:15][::-1].plot.barh(figsize=(8, 4), color='skyblue')
plt.xlabel('Values')
plt.title('Top 15 Countries')


# Displaying the value of each bar on the plot

for i, v in enumerate(countries[:15][::-1]):
    ax.text(v + 500, i, str(v), color='black', va='center', fontsize=10)

plt.show()

In [ ]:
# Print new dataset

food_countries = splitDataFrameList(food_table, "ingredients_tags", ",")
countries = food_countries["ingredients_tags"].str.split(',').explode().str.strip().value_counts()

In [ ]:
# Plotting the horizontal bar chart

ax = countries[:15][::-1].plot.barh(figsize=(8, 4), color='skyblue')
plt.xlabel('Values')
plt.title('Top 15 Countries')


# Displaying the value of each bar on the plot

for i, v in enumerate(countries[:15][::-1]):
    ax.text(v + 500, i, str(v), color='black', va='center', fontsize=10)

plt.show()

In [ ]:
print(countries)

In [ ]:
countries.to_csv(path + '/data/ingredients.tsv', sep='\t', index=True)

## Populate DB

In [12]:
# Load the required libraries
from rdflib import Graph, Literal, RDF, URIRef, Namespace
# rdflib knows about some namespaces, like FOAF
from rdflib.namespace import FOAF, XSD, SKOS

In [13]:
# Construct the country and the movie ontology namespaces not known by RDFlib
CNS = Namespace("http://eulersharp.sourceforge.net/2003/03swap/countries#")
FO = Namespace("http://www.graphle.com/foodOntology#")

In [46]:
def capitalize_first_letters(text):
    return ' '.join(str(text).split('-')).title()

def remove_language_tag(text):
    split_text = re.split(':', str(text))
    
    if len(split_text) > 1:
        return split_text[1]
    print("No language tag in " + str(text))
    return split_text[0]

def create_tag(text):
    lower = str(text).lower().strip()
    cleared = re.sub(r'[^\p{L}\d\s-]', "", lower, flags=re.UNICODE)
    return '-'.join(cleared.split())

def split_tags(text):
    return str(text).split(',')

def filter_tags(text, dictionary):
    result = []
    if pd.isna(text):
        return result
    
    splitted = split_tags(text)
    
    for item in splitted:
        if item in dictionary:
            result.append(dictionary[item])
    return result

def match_items(items, dictionary):
    out = []
    if pd.isna(items) or items == '':
        return out
    
    item_list = re.split(',', items)
    for item in item_list:
        key_added = False
        for key in dictionary:
            if key_added:
                break
            for name in dictionary[key][1]:
                if item == name:
                    out.append(key)
                    key_added = True
                    break
    return out

def match_labels(labels, dictionary):
    out = []
    if pd.isna(labels) or labels == '':
        return out
    
    label_list = re.split(',', labels)
    formatted_label_list = []
    for label in label_list:
        label = re.sub('"', "'", re.sub('--+', '-', label.strip().lower().replace(' ', '-')))
        if re.match('^[a-z]{2}:', label):
            formatted_label_list.append(label)
        else:
            formatted_label_list.append(f"en:{label}")
            
    for label in formatted_label_list:
        key_added = False
        for key in dictionary:
            if key_added:
                break
            for name in dictionary[key][1]:
                if name == label:
                    out.append(key)
                    key_added = True
                    break
    return out
    

### SKOS Taxonomy

In [ ]:
#create the graph
g = Graph()

# Bind the namespaces to a prefix for more readable output
g.bind("foaf", FOAF)
g.bind("xsd", XSD)
g.bind("countries", CNS)
g.bind("fo", FO)
g.bind("skos", SKOS)

In [ ]:
for key in ing_dict:
    Ingredient = URIRef(FO[re.sub('>', 'greater-than', re.sub("%", "%25", key))])
    g.add((Ingredient, RDF.type, FO.Ingredient))
    g.add((Ingredient, RDF.type, SKOS.Concept))
    for super_ing in ing_dict[key][0]:
        g.add((Ingredient, SKOS.broaderTransitive, URIRef(FO[re.sub('>', 'greater-than', re.sub("%", "%25", super_lab))])))
    for name in ing_dict[key][1]:
        split_name = re.split(':', name)
        g.add((Ingredient, FO['ingredientName'], Literal(split_name[1], lang=split_name[0])))
        
for key in add_dict:
    Additive = URIRef(FO[re.sub('>', 'greater-than', re.sub("%", "%25", key))])
    g.add((Additive, RDF.type, FO.Additive))
    g.add((Additive, RDF.type, SKOS.Concept))
    for super_add in add_dict[key][0]:
        g.add((Additive, SKOS.broaderTransitive, URIRef(FO[re.sub('>', 'greater-than', re.sub("%", "%25", super_lab))])))
    for name in add_dict[key][1]:
        split_name = re.split(':', name)
        g.add((Additive, FO['ingredientName'], Literal(split_name[1], lang=split_name[0])))
        
        
for key in vit_dict:
    Vitamin = URIRef(FO[re.sub('>', 'greater-than', re.sub("%", "%25", key))])
    g.add((Vitamin, RDF.type, FO.Vitamin))
    g.add((Vitamin, RDF.type, SKOS.Concept))
    for super_vit in vit_dict[key][0]:
        g.add((Vitamin, SKOS.broaderTransitive, URIRef(FO[re.sub('>', 'greater-than', re.sub("%", "%25", super_lab))])))
    for name in vit_dict[key][1]:
        split_name = re.split(':', name)
        g.add((Vitamin, FO['ingredientName'], Literal(split_name[1], lang=split_name[0])))
    
for key in pack_dict:
    Packaging = URIRef(FO[re.sub('>', 'greater-than', re.sub("%", "%25", key))])
    g.add((Packaging, RDF.type, FO.Packaging))
    g.add((Packaging, RDF.type, SKOS.Concept))
    for super_pack in pack_dict[key][0]:
        g.add((Packaging, SKOS.broaderTransitive, URIRef(FO[re.sub('>', 'greater-than', re.sub("%", "%25", super_lab))])))
    for name in pack_dict[key][1]:
        split_name = re.split(':', name)
        g.add((Packaging, FO['packagingName'], Literal(split_name[1], lang=split_name[0])))
    
    
for key in lab_dict:
    Label = URIRef(FO[re.sub('>', 'greater-than', re.sub("%", "%25", key))])
    g.add((Label, RDF.type, FO.Label))
    g.add((Label, RDF.type, SKOS.Concept))
    for super_lab in lab_dict[key][0]:
        g.add((Label, SKOS.broaderTransitive, URIRef(FO[re.sub('>', 'greater-than', re.sub("%", "%25", super_lab))])))
    for name in lab_dict[key][1]:
        split_name = re.split(':', name)
        g.add((Label, FO['labelName'], Literal(split_name[1], lang=split_name[0])))

In [ ]:
# print all the data in the Turtle format
print("--- saving serialization ---")
with open(savePath + 'taxonomy.ttl', 'w', encoding='utf-8') as file:
    file.write(g.serialize(format='turtle'))

### Brand

In [55]:
#create the graph
g = Graph()

# Bind the namespaces to a prefix for more readable output
g.bind("foaf", FOAF)
g.bind("xsd", XSD)
g.bind("countries", CNS)
g.bind("fo", FO)

In [56]:
#iterate over the league dataframe
for index, row in food_table.iterrows():
    # Create the node to add to the Graph
    # the node has the namespace + the league id as URI
    idU = create_tag(row['brands_tags'])
    
    
    if not pd.isna(idU) and not idU == '':
        Brand = URIRef(FO[idU])
        # Add triples using store's add() method.
        if not (Brand, None, None) in g:   
            g.add((Brand, RDF.type, FO.Brand))
            if not pd.isna(row['brands']):
                g.add((Brand, FO['name'], Literal(capitalize_first_letters(row['brands']), datatype=XSD.string)))  
            else:
                g.add((Brand, FO['name'], Literal(capitalize_first_letters(row['brands_tags']), datatype=XSD.string)))
            if not pd.isna(row['brand_owner']):
                g.add((Brand, FO['owner'], Literal(row['brand_owner'], datatype=XSD.string)))
    
    
    if index % 2500 == 0 :
        print(f"Progress: {index/food_table.shape[0]*100:.2f}%")
        
    if index == 10000:
        break

Progress: 0.00%
Progress: 0.34%
Progress: 0.68%
Progress: 1.01%
Progress: 1.35%


In [57]:
# print all the data in the Turtle format
print("--- saving serialization ---")
with open(savePath + 'brand.ttl', 'w', encoding='utf-8') as file:
    file.write(g.serialize(format='turtle'))

--- saving serialization ---


### FoodGroup

In [58]:
#create the graph
g = Graph()

# Bind the namespaces to a prefix for more readable output
g.bind("foaf", FOAF)
g.bind("xsd", XSD)
g.bind("countries", CNS)
g.bind("fo", FO)

In [59]:
#iterate over the league dataframe
for index, row in food_table.iterrows():
    # Create the node to add to the Graph
    # the node has the namespace + the league id as URI
    idU = row['food_groups']
    if not pd.isna(idU):
        
        idU = remove_language_tag(row['food_groups'])
        FoodGroup = URIRef(FO[idU])
        # Add triples using store's add() method.
        if not (FoodGroup, None, None) in g:   
            g.add((FoodGroup, RDF.type, FO.FoodGroup))
            g.add((FoodGroup, FO['name'], Literal(capitalize_first_letters(idU), datatype=XSD.string)))  
    
    
    if index % 2500 == 0 :
        print(f"Progress: {index/food_table.shape[0]*100:.2f}%")
        
    if index == 10000:
        break

Progress: 0.00%
Progress: 0.34%
Progress: 0.68%
Progress: 1.01%
Progress: 1.35%


In [60]:
# print all the data in the Turtle format
print("--- saving serialization ---")
with open(savePath + 'foodgroups.ttl', 'w') as file:
    file.write(g.serialize(format='turtle'))

--- saving serialization ---


### Product

In [61]:
#create the graph
g = Graph()

# Bind the namespaces to a prefix for more readable output
g.bind("foaf", FOAF)
g.bind("xsd", XSD)
g.bind("countries", CNS)
g.bind("fo", FO)

In [62]:
#iterate over the league dataframe
for index, row in food_table.iterrows():
    # Create the node to add to the Graph
    # the node has the namespace + the league id as URI
    idU = create_tag(row['product_name']) + '-' + str(row['code'])
    
    if idU.startswith('-'):
        continue
    
    Product = URIRef(FO[idU])
    
    # Add triples using store's add() method.
    g.add((Product, RDF.type, FO.Product))
    g.add((Product, FO['name'], Literal(row['product_name'], datatype=XSD.string)))  
    if not pd.isna(row['serving_size']):
        g.add((Product, FO['servingSize'], Literal(row['serving_size'], datatype=XSD.string)))
    if not pd.isna(row['nutriscore_score']):
        g.add((Product, FO['nutriscoreScore'], Literal(row['nutriscore_score'], datatype=XSD.float)))
    if not pd.isna(row['nutriscore_grade']):
        g.add((Product, FO['nutriscoreGrade'], Literal(row['nutriscore_grade'], datatype=XSD.string)))
    if not pd.isna(row['nova_group']):
        g.add((Product, FO['novaGroup'], Literal(row['nova_group'], datatype=XSD.float)))
    if not pd.isna(row['nova_group']):
        g.add((Product, FO['ecoscoreGrade'], Literal(row['ecoscore_grade'], datatype=XSD.string)))   
    g.add((Product, FO['energyKJ'], Literal(row['energy_100g'], datatype=XSD.float)))
    g.add((Product, FO['energyKcal'], Literal(row['energy-kcal_100g'], datatype=XSD.float)))
    g.add((Product, FO['fat'], Literal(row['fat_100g'], datatype=XSD.float)))
    if not pd.isna(row['saturated-fat_100g']):
        g.add((Product, FO['fatSaturated'], Literal(row['saturated-fat_100g'], datatype=XSD.float)))
    if not pd.isna(row['trans-fat_100g']):
        g.add((Product, FO['fatTrans'], Literal(row['trans-fat_100g'], datatype=XSD.float)))
    if not pd.isna(row['cholesterol_100g']):    
        g.add((Product, FO['cholesterol'], Literal(row['cholesterol_100g'], datatype=XSD.float)))
    g.add((Product, FO['carbohydrates'], Literal(row['carbohydrates_100g'], datatype=XSD.float)))
    if not pd.isna(row['sugars_100g']):
        g.add((Product, FO['sugars'], Literal(row['sugars_100g'], datatype=XSD.float)))
    if not pd.isna(row['fiber_100g']):
        g.add((Product, FO['fiber'], Literal(row['fiber_100g'], datatype=XSD.float)))
    g.add((Product, FO['proteins'], Literal(row['proteins_100g'], datatype=XSD.float)))
    if not pd.isna(row['salt_100g']):
        g.add((Product, FO['salt'], Literal(row['salt_100g'], datatype=XSD.float)))
    if not pd.isna(row['sodium_100g']):
        g.add((Product, FO['sodium'], Literal(row['sodium_100g'], datatype=XSD.float)))
    if not pd.isna(row['vitamin-a_100g']):    
        g.add((Product, FO['vitaminA'], Literal(row['vitamin-a_100g'], datatype=XSD.float)))
    if not pd.isna(row['vitamin-c_100g']):
        g.add((Product, FO['vitaminC'], Literal(row['vitamin-c_100g'], datatype=XSD.float)))
    if not pd.isna(row['calcium_100g']):
        g.add((Product, FO['calcium'], Literal(row['calcium_100g'], datatype=XSD.float)))
    if not pd.isna(row['iron_100g']):
        g.add((Product, FO['irom'], Literal(row['iron_100g'], datatype=XSD.float)))
    
    # CI SONO DEGLI UNKNOWN
    
    if index % 2500 == 0 :
        print(f"Progress: {index/food_table.shape[0]*100:.2f}%")
        
    if index == 10000:
        break

Progress: 0.00%
Progress: 0.34%
Progress: 0.68%
Progress: 1.01%
Progress: 1.35%


In [63]:
# print all the data in the Turtle format
print("--- saving serialization ---")
with open(savePath + 'product.ttl', 'w', encoding='utf-8') as file:
    file.write(g.serialize(format='turtle'))

--- saving serialization ---


### Product Join

In [66]:
#create the graph
g = Graph()

# Bind the namespaces to a prefix for more readable output
g.bind("foaf", FOAF)
g.bind("xsd", XSD)
g.bind("countries", CNS)
g.bind("fo", FO)

In [67]:
#iterate over the league dataframe
for index, row in food_table.iterrows():
    # Create the node to add to the Graph
    # the node has the namespace + the league id as URI
    idPr = create_tag(row['product_name']) + '-' + str(row['code'])
    idBr = create_tag(row['brands_tags'])
    idFG = row['food_groups']
    
    if idPr.startswith('-'):
        continue
    Product = URIRef(FO[idPr])
    
    # Join with Brand
    if not pd.isna(idBr) and not idBr == '':
        
        Brand = URIRef(FO[idBr])
        
        g.add((Product, FO['hasBrand'], Brand))

    # Join with FoodGroup
    if not pd.isna(idFG):
        
        idFG = remove_language_tag(row['food_groups'])
        FoodGroup = URIRef(FO[idFG])
        
        g.add((Product, FO['belongsToGroup'], FoodGroup))
        
    # Join with Ingredient
    ing_matched = match_items(row['ingredients_tags'], ing_dict)
    for ingredient in ing_matched:
        
        idIn = re.sub('>', 'greater-than', re.sub("%", "%25", ingredient))
        Ingredient = URIRef(FO[idIn])
        
        g.add((Product, FO['hasIngredient'], Ingredient))
    
    # Join with Additive
    add_matched = match_items(row['ingredients_tags'], add_dict)
    for additive in add_matched:
        
        idAd = re.sub('>', 'greater-than', re.sub("%", "%25", additive))
        Additive = URIRef(FO[idAd])
        
        g.add((Product, FO['hasIngredient'], Additive))
    
    # Join with Vitamin
    vit_matched = match_items(row['ingredients_tags'], vit_dict)
    for vitamin in vit_matched:
        
        idVi = re.sub('>', 'greater-than', re.sub("%", "%25", vitamin))
        Vitamin = URIRef(FO[idVi])
        
        g.add((Product, FO['hasIngredient'], Vitamin))
    
    # Join with Packaging
    pack_matched = match_items(row['packaging_tags'], pack_dict)
    for packaging in pack_matched:
        
        idPk = re.sub('>', 'greater-than', re.sub("%", "%25", packaging))
        Packaging = URIRef(FO[idPk])
        
        g.add((Product, FO['hasPackaging'], Packaging))
    
    # Join with Label
    lab_matched = match_labels(row['labels_en'], lab_dict)
    for label in lab_matched:
        
        idLb = re.sub('>', 'greater-than', re.sub("%", "%25", label))
        Label = URIRef(FO[idLb])
        
        g.add((Product, FO['hasLabel'], Label))
    
    
    if index % 2500 == 0 :
        print(f"Progress: {index/food_table.shape[0]*100:.2f}%")
        
    if index == 10000: #100000
        break

Progress: 0.00%
Progress: 0.34%
Progress: 0.68%
Progress: 1.01%
Progress: 1.35%


In [68]:
# print all the data in the Turtle format
print("--- saving serialization ---")
with open(savePath + 'product_join.ttl', 'w', encoding='utf-8') as file:
    file.write(g.serialize(format='turtle'))

--- saving serialization ---


In [69]:
#Join the separate serializations

import shutil

with open(savePath + 'food_database.ttl','wb') as wfd:
    for f in [savePath + 'taxonomy.ttl', savePath + 'product.ttl', savePath + 'brand.ttl', savePath + 'foodgroups.ttl', savePath + 'product_join.ttl']:
        with open(f,'rb') as fd:
            shutil.copyfileobj(fd, wfd)
            wfd.write(b"\n\n\n")